<a href="https://colab.research.google.com/github/raul27868/03MAIR---Algoritmos-de-Optimizacion---2020/blob/master/AG1/Algoritmos_horario_clasesV3.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
#Cursos: 1 a 6, linea 2(letras A y B)

#Materias y horas a la semana:
#  'MATERIAS' : {'LEN':5,'MAT':5,'ING':4,'EFI':3,'NAT':3,'SOC':3,'LIB':3,'REL':2,'ART':2, 


#Profesores:15
#1-10   PRIMARIA: LEN,MAT,SOC,NAT,ART
#11-13  INGLES  : LEN,MAT,SOC,NAT,ART,ING
#14-15  E.FISICA: LEN,MAT,SOC,NAT,ART,EFI
#1-4    DEI     : REL                     Para dar religion hay que tener el DEI. Lo tiene 1-4 de PRIMARIA 

# 27 horas a la semana de cada curso/letra. 6 horas a la semana (sobran 3 horas que quedan libres)

 

In [0]:
import random

import copy   #Para copiar listas

import json 

import operator              #para usar #para usar el operator.concat con reduce
from functools import reduce #para usar el reduce

import statistics     #Para el calculo de la desviacion estandar
import numpy as np

from itertools import chain  #Para combinar listas

import datetime  #Conocer tiempo actual

#Define la funcion sign 0=positivo, -1=negativo
sign = lambda x: (0, -1)[x<0]

#Seleciona n elementos al azar de una lista(esto ya lo hace random.sample)
def select(data,n):
  if len(data)<n:
    return None
  RET = []
  for i in range(n):
    p = random.choice(list(set(data)-set(RET)))
    RET.append(p)
  return RET

#Obtiene los profesores que pueden dar una materia
def get_profesores(M,PROFESORES):
  RET = []
  for p,m in PROFESORES.items():
    RET.append(p if M in m else None) if (p if M in m else None) else None
  return RET

In [0]:
#Parametros del problema
PARAMETROS = {
  'CURSOS':[1,2,3,4,5,6], 

  'LETRAS':['A','B'],

  'HORAS':6,
  #DIAS. Se asume que son 5 dias a la semana

  #Materias y horas por semana. Ordenar por numero de horas
  'MATERIAS' : {'LEN':5,'MAT':5,'ING':4,'EFI':3,'NAT':3,'SOC':3,'LIB':3,'REL':2,'ART':2, 
                   
                },

  'MAX_HORAS_X_PROFESOR' : 23,

  'PROFESORES' :{
    1:['LEN'  ,'MAT' ,'NAT' ,'SOC'      ,'REL' ,'ART' ],
    2:['LEN'  ,'MAT' ,'NAT' ,'SOC'      ,'REL' ,'ART' ],
    3:['LEN'  ,'MAT' ,'NAT' ,'SOC'      ,'REL' ,'ART' ],
    4:['LEN'  ,'MAT' ,'NAT' ,'SOC'      ,'REL' ,'ART' ],
    5:['LEN'  ,'MAT' ,'NAT' ,'SOC'             ,'ART' ],
    6:['LEN'  ,'MAT' ,'NAT' ,'SOC'             ,'ART' ],
    7:['LEN'  ,'MAT' ,'NAT' ,'SOC'             ,'ART' ],
    8:['LEN'  ,'MAT' ,'NAT' ,'SOC'             ,'ART' ],
    9:['LEN'  ,'MAT' ,'NAT' ,'SOC'             ,'ART' ],
    10:['LEN'  ,'MAT' ,'NAT' ,'SOC' ,'ING'     ,'ART' ],
    11:['LEN'  ,'MAT' ,'NAT' ,'SOC' ,'ING'     ,'ART' ],
    12:['LEN'  ,'MAT' ,'NAT' ,'SOC' ,'ING'     ,'ART' ],
    13:['LEN'  ,'MAT' ,'NAT' ,'SOC' ,'ING'     ,'ART' ],
    14:['LEN'  ,'MAT' ,'NAT' ,'SOC'            ,'ART','EFI' ],
    15:['LEN'  ,'MAT' ,'NAT' ,'SOC'            ,'ART','EFI' ],
    16:['LIB'],
    17:['LIB' ],
    #18:['LEN'  ,'MAT' ,'NAT' ,'SOC' ,'ING'     ,'ART' ],

  }
  
 
}

In [0]:

#Evalua la solucion solo con los profesores penalizando fuerte los profesores que se pasan de MAX_HORAS_X_PROFESOR horas(23) asignadas
#   y debil con los que no llegan 

def evalua_solucion_profesores(SOLUCION, PARAMETROS , imprime=0):
    VALOR = 0
    #Penaliza cada hora que se pasa del máximo de MAX_HORAS_X_PROFESOR por cada profesor. Con peso 10
    #  Calcula el numero de horas por cada profesor sin tener en cuenta los profesroes ficticios asociados a las materias 'LIB'
    SUM_HORAS_PROFES= sum_horas_profes(SOLUCION, PARAMETROS)
    for x in SUM_HORAS_PROFES:
      if x['horas'] > PARAMETROS['MAX_HORAS_X_PROFESOR'] and 'LIB' not in list(map(lambda x:x[2:5],x['s']))  :
        VALOR += 10000*(x['horas'] - PARAMETROS['MAX_HORAS_X_PROFESOR'])

    #Se penaliza por cada profresor que no cumple el maximo de horas pero con menos peso. Con peso 100. Excepto si no tiene horas asignadas, entoces no hace falta ese profe  
    #Se penaliza la variabilidad del total de horas de los profesores que no tienen el maximo de horas(PROFES_NO_COMPLETA)
    #No tiene en cuenta los profesores ficticios asociados a las materias 'LIB'
    PROFES_NO_COMPLETA=[]
    for x in SUM_HORAS_PROFES:
      if x['horas'] < PARAMETROS['MAX_HORAS_X_PROFESOR'] and x['horas'] > 0 and 'LIB' not in list(map(lambda x:x[2:5],x['s'])):
        #print("Añade a " , x['profe'] , " con " , x['horas'])
        VALOR += 1000
        PROFES_NO_COMPLETA.append(x['horas'])

    #Se penaliza 
    #  1º la variabilidad de los cursos asignados a cada profesor. Por ejemplo el peor caso es que un profesor de materias en 1,2,3,4,5,6
    #    por el contrario el mejor caso es que un profesor de solo en un curso
    #  2º ademas se penaliza tambien la diferencia de cursos. Por ejemplo es peor dar 1º y 6º que 1º y 2º
    #1º
    PROFES_CURSOS= [ [p,set([m[0] for m,v in SOLUCION.items() if v['profe'] == p ])]     for p in PARAMETROS['PROFESORES'] if 'LIB' not in PARAMETROS['PROFESORES'][p] ]
    VALOR += sum([ len(x[1])  for x in PROFES_CURSOS   ])

    #2º
    VALOR += sum([  sum([   int(j)-int(i)   for indi, i in enumerate(sorted(list(x[1]),reverse=True)) for indj,j in enumerate(sorted(list(x[1]),reverse=True)) if indi>indj ])  for indx, x in enumerate(PROFES_CURSOS )])

    #Se penaliza con 1/10 por la desviacion de las horas incompletas de los profesores que no dan el total de horas MAX_HORAS_X_PROFESOR
    #print(PROFES_NO_COMPLETA,statistics.stdev(PROFES_NO_COMPLETA))
    if len(PROFES_NO_COMPLETA) > 1:
      VALOR += statistics.stdev(PROFES_NO_COMPLETA)/10
    



    #MEJORAR con preferencias de los profesores dando un peso menor que los anteriores
    
    return VALOR

In [0]:
S={"1ALEN": {"profe": 9}, "1AMAT": {"profe": 14}, "1AING": {"profe": 13}, "1AEFI": {"profe": 14}, "1ANAT": {"profe": 4}, "1ASOC": {"profe": 12}, "1ALIB": {"profe": 16}, "1AREL": {"profe": 2}, "1AART": {"profe": 2}, "1BLEN": {"profe": 3}, "1BMAT": {"profe": 12}, "1BING": {"profe": 13}, "1BEFI": {"profe": 14}, "1BNAT": {"profe": 12}, "1BSOC": {"profe": 2}, "1BLIB": {"profe": 16}, "1BREL": {"profe": 4}, "1BART": {"profe": 2}, "2ALEN": {"profe": 6}, "2AMAT": {"profe": 9}, "2AING": {"profe": 10}, "2AEFI": {"profe": 14}, "2ANAT": {"profe": 5}, "2ASOC": {"profe": 13}, "2ALIB": {"profe": 16}, "2AREL": {"profe": 3}, "2AART": {"profe": 10}, "2BLEN": {"profe": 9}, "2BMAT": {"profe": 2}, "2BING": {"profe": 12}, "2BEFI": {"profe": 14}, "2BNAT": {"profe": 9}, "2BSOC": {"profe": 6}, "2BLIB": {"profe": 16}, "2BREL": {"profe": 3}, "2BART": {"profe": 12}, "3ALEN": {"profe": 2}, "3AMAT": {"profe": 11}, "3AING": {"profe": 13}, "3AEFI": {"profe": 15}, "3ANAT": {"profe": 4}, "3ASOC": {"profe": 8}, "3ALIB": {"profe": 17}, "3AREL": {"profe": 1}, "3AART": {"profe": 6}, "3BLEN": {"profe": 1}, "3BMAT": {"profe": 8}, "3BING": {"profe": 13}, "3BEFI": {"profe": 15}, "3BNAT": {"profe": 8}, "3BSOC": {"profe": 4}, "3BLIB": {"profe": 16}, "3BREL": {"profe": 1}, "3BART": {"profe": 11}, "4ALEN": {"profe": 3}, "4AMAT": {"profe": 11}, "4AING": {"profe": 11}, "4AEFI": {"profe": 14}, "4ANAT": {"profe": 12}, "4ASOC": {"profe": 6}, "4ALIB": {"profe": 16}, "4AREL": {"profe": 2}, "4AART": {"profe": 3}, "4BLEN": {"profe": 4}, "4BMAT": {"profe": 3}, "4BING": {"profe": 13}, "4BEFI": {"profe": 14}, "4BNAT": {"profe": 12}, "4BSOC": {"profe": 6}, "4BLIB": {"profe": 16}, "4BREL": {"profe": 3}, "4BART": {"profe": 2}, "5ALEN": {"profe": 7}, "5AMAT": {"profe": 4}, "5AING": {"profe": 10}, "5AEFI": {"profe": 15}, "5ANAT": {"profe": 7}, "5ASOC": {"profe": 11}, "5ALIB": {"profe": 17}, "5AREL": {"profe": 1}, "5AART": {"profe": 6}, "5BLEN": {"profe": 6}, "5BMAT": {"profe": 9}, "5BING": {"profe": 10}, "5BEFI": {"profe": 15}, "5BNAT": {"profe": 10}, "5BSOC": {"profe": 1}, "5BLIB": {"profe": 16}, "5BREL": {"profe": 4}, "5BART": {"profe": 10}, "6ALEN": {"profe": 7}, "6AMAT": {"profe": 7}, "6AING": {"profe": 11}, "6AEFI": {"profe": 15}, "6ANAT": {"profe": 15}, "6ASOC": {"profe": 8}, "6ALIB": {"profe": 17}, "6AREL": {"profe": 1}, "6AART": {"profe": 7}, "6BLEN": {"profe": 1}, "6BMAT": {"profe": 8}, "6BING": {"profe": 10}, "6BEFI": {"profe": 15}, "6BNAT": {"profe": 7}, "6BSOC": {"profe": 8}, "6BLIB": {"profe": 17}, "6BREL": {"profe": 1}, "6BART": {"profe": 15}}
asignaturas_impartidas_x_profesor(S)

In [0]:
#Genera una solucion GRASP solo con profesores
#  Se ordenan las asignaturas por orden de curso.
#  Se van asignando por orden(con componente aleatorio) para que la distribución sea
#  lo mas homogenea posible. 
def genera_solucion_profesores_GRASP(PARAMETROS):
  SOLUCION={}
  ASIGNATURAS = [ str(c)+str(l)+str(m) for c in PARAMETROS['CURSOS'] for l in PARAMETROS['LETRAS'] for m,h in PARAMETROS['MATERIAS'].items()  ]

  
  for profe in PARAMETROS['PROFESORES']:
    tmp_horas =0
    while tmp_horas < PARAMETROS['MAX_HORAS_X_PROFESOR']:
      #print("\t", [x for x in ASIGNATURAS if x[2:5] in PARAMETROS['PROFESORES'][profe] ])
      try:  
        asignatura  = random.choice([x for x in ASIGNATURAS if x[2:5] in PARAMETROS['PROFESORES'][profe] ][:min(10,len(ASIGNATURAS))])
      except IndexError:
        asignatura =""
        tmp_horas =10e10
        next
      #print("\t", profe,asignatura)
      if profe in get_profesores(asignatura[2:5],PARAMETROS['PROFESORES']) and asignatura:
        ASIGNATURAS.remove(asignatura)
        SOLUCION[asignatura] = {"profe":profe, } 
        tmp_horas += PARAMETROS['MATERIAS'][asignatura[2:5]]
        #print(profe,asignatura,tmp_horas)
    #print(SOLUCION)

    #Revisa la asignaturas que no se han asignado
  #print("**********",set([ str(c)+str(l)+str(m) for c in PARAMETROS['CURSOS'] for l in PARAMETROS['LETRAS'] for m,h in PARAMETROS['MATERIAS'].items()  ]) - set(SOLUCION.keys()))

  for asig in set([ str(c)+str(l)+str(m) for c in PARAMETROS['CURSOS'] for l in PARAMETROS['LETRAS'] for m,h in PARAMETROS['MATERIAS'].items()  ]) - set(SOLUCION.keys()):
    SOLUCION[asig] = {"profe": random.choice( [p  for p,MATERIAS in PARAMETROS['PROFESORES'].items() if asig[2:5] in MATERIAS   ]) }
  #print("**********",set([ str(c)+str(l)+str(m) for c in PARAMETROS['CURSOS'] for l in PARAMETROS['LETRAS'] for m,h in PARAMETROS['MATERIAS'].items()  ]) - set(SOLUCION.keys()))
 
  return SOLUCION


_ = genera_solucion_profesores_GRASP(PARAMETROS)
print(json.dumps(_))
evalua_solucion_profesores(_, PARAMETROS  )
asignaturas_impartidas_x_profesor(_)

In [0]:
asig='4BREL'
[p  for p,MATERIAS in PARAMETROS['PROFESORES'].items() if asig[2:5] in MATERIAS   ]

[1, 2, 3, 4]

In [0]:
#Genera una solucion aleatoria solo con profesores
def genera_solucion_profesores(PARAMETROS):
  SOLUCION={}
  for c in PARAMETROS['CURSOS']:
    for l in PARAMETROS['LETRAS']:
      for m,h in PARAMETROS['MATERIAS'].items():
        #print(m,h)
        profe = random.choice(get_profesores(m,PARAMETROS['PROFESORES'])) #MEJORA. Elejir según una distribución inversa a los profes ya elegidos

        SOLUCION[str(c)+str(l)+str(m)] = {"profe":profe, } 
  return  SOLUCION 


def sum_horas_profes(SOLUCION, PARAMETROS):
    PROF = {} #Asigna a cada profe las asignaturas que da
    for c,p in SOLUCION.items():
      if p['profe'] in PROF  :
        PROF[p['profe']].append(c)
      else:
        PROF[p['profe']] = [c]

    return  list(map(lambda x:{"profe":x[0],"horas": sum( map(lambda y:PARAMETROS['MATERIAS'][y[2:5]] , x[1]) ), "s":x[1] } ,PROF.items() )   )
 

  

#################################################################
#ALGORITMO GENETICO V3
#Modelo:
#   cromosomas(genes) : curso/letra/materia=clase
#   alelos            : profesor/dia/hora/

#Parametros del algoritmo genético 
N_POBLACION = 200         #Numero de individuos en cada población  
N_PUNTOS_DE_CRUCE = 4     #Numero de puntos de cruce para hacer el cruce entre padres. 
N_MUTACION = 5            #Numero de maximo de genes que se van a mutar en cada generacion  
N_HIJOS    = 4            #Numero de hijos generados en cada cruce

#Se toma como idea la realizacion de la asignacion por fases de  https://pdfs.semanticscholar.org/eb88/17d24497222102845fdaa5e8759db86a7a9e.pdf
#  En una primera fase se asigna el profesor a la clase=curso/letra/materia y en la segunda el dia/hora
#  Por tanto tenemos cromo somas dobles uno por cada fase y por tanto dobles genes, uno para el profesor y otro para el dia/hora.
#  Se realizará primero la asignacion de profesores y luego horarios.

#Proceso principal de algoritmo genetico para obtener solucion solo con profesores: 1ª fase
def main_profesores(PARAMETROS, N_POBLACION, N_PUNTOS_DE_CRUCE, N_MUTACION, N_HIJOS):
  
  MEJOR_VALOR_ENCONTRADO = 10000000000
  MEJOR_SOLUCION={}
  
  POBLACION = [genera_solucion_profesores(PARAMETROS) for i in range(N_POBLACION )]
  #POBLACION = [genera_solucion_profesores_GRASP(PARAMETROS) for i in range(N_POBLACION )]
  
  #Asigna todas las clases posibles "1ALEN", "1AMAT", ...
  CLASES = [k for k,v in POBLACION[0].items() ]

   
  
  CRITERIO_PARADA = False
  iteracion = 0
  
  while(CRITERIO_PARADA == False):
    iteracion +=1
    
    #Añade un 10% de poblacion en cada iteracion
    POBLACION = POBLACION + [genera_solucion_profesores(PARAMETROS) for i in range( N_POBLACION//10 )]
    #POBLACION = POBLACION + [genera_solucion_profesores_GRASP(PARAMETROS) for i in range( N_POBLACION//10 )]


    #Ordena la poblacion y se queda con los mejor valorados. MEJORA.Elegir otro metodo para favorecer aleatoriamente a peores(ruleta)
    ORDENACION= []
    ORDENACION =  list(map(lambda x: {"v":evalua_solucion_profesores(x, PARAMETROS),'s':x} ,POBLACION) ) 
    ORDENACION.sort(key=lambda x: x['v'])
    
    POBLACION = []
    POBLACION = list(map(lambda x:x['s'],ORDENACION[0:N_POBLACION]))
    
    #Imprime el mejor resultado obtenido cada 10 iteraciones
    if iteracion/50 == iteracion//50:
      print("Iteracion:", iteracion)
      print("mejor solucion:" , MEJOR_VALOR_ENCONTRADO , json.dumps(POBLACION[0] ) )
      print(list(map(lambda   x:x['v'],ORDENACION)))
      print()
    
    #Cruce
    #  Genera una copia de la poblacion para ir eliminando los padres elegidos
    POBLACION_COPIA = []
    POBLACION_COPIA = copy.deepcopy(POBLACION)
    
    if ORDENACION[0]['v'] < MEJOR_VALOR_ENCONTRADO:
      MEJOR_VALOR_ENCONTRADO = ORDENACION[0]['v']
      MEJOR_SOLUCION = ORDENACION[0]['v']
    
    i_cruce=0
    while(len(POBLACION_COPIA) > 1   ):
      i_cruce+=1
      #print("Cruce:",i_cruce)
      padres = [] #Variable que contiene los padres
    
      #Elige el padre1
      padres.append(random.choice(POBLACION_COPIA))
      POBLACION_COPIA.remove(padres[0])

      #Elige el padre2
      padres.append(random.choice(POBLACION_COPIA))
      POBLACION_COPIA.remove(padres[1])
      
      
      HIJOS =[]  #Array que contiene los hijos generados
      #Cruce uniforme aleatorio. PENDINTE: Probar con otros operadores
      for i in range(N_HIJOS):
        HIJOS.append( {x:padres[random.choice([0,1])][x] for x in CLASES })

        #Hace mutacion si el hijo no es mejor que lo encontrado hasta el momento(Conservacion de buenos hijos)
        if evalua_solucion_profesores(HIJOS[i],PARAMETROS) >= MEJOR_VALOR_ENCONTRADO:
          genes_a_mutar = select([k for k,v in padres[0].items() ], random.choice(range(N_MUTACION)) )
          for gen in genes_a_mutar:
            HIJOS[i][gen]["profe"] =  select(get_profesores(gen[2:6],PARAMETROS['PROFESORES']) ,1)[0]
    
      #Se añaden los hijos a la poblacion
      POBLACION.extend(HIJOS)
    
    
    
    if iteracion == 10000  or MEJOR_VALOR_ENCONTRADO ==0:
      print("Mejor solucion encontrada con valor:" , evalua_solucion_profesores(POBLACION[0],PARAMETROS) , json.dumps(POBLACION[0]) )
      CRITERIO_PARADA = True
  
  return POBLACION
    
    
    
  

In [0]:
 __POB = main_profesores(PARAMETROS, N_POBLACION, N_PUNTOS_DE_CRUCE, N_MUTACION, N_HIJOS)



In [0]:
def asignaturas_impartidas_x_profesor(S_INPUT):
  RET={}
  for k,v in S_INPUT.items():
    if v['profe'] not in RET:
      RET[v['profe']] =[]
    RET[v['profe']].append(k)
  #con (PARAMETROS['MATERIAS'][y[2:5]] if isinstance(y, str)    else y) +    (PARAMETROS['MATERIAS'][x[2:5]] if isinstance(x, str)    else x) , v)      }} for k,v in RET.items() 
  #  se calculan el total de horas de un profesor
  TH = [{k:{'m':v,"total_materias":len(v), "total_horas": reduce(lambda x,y:  (PARAMETROS['MATERIAS'][y[2:5]] if isinstance(y, str)    else y) +    (PARAMETROS['MATERIAS'][x[2:5]] if isinstance(x, str)    else x) , v)      }} for k,v in RET.items()]

  #print(TH)  
  for [x,y,z] in sorted([[list(x.keys())[0]  , x[list(x.keys())[0]]['total_horas'] , x[list(x.keys())[0]]['m']] for x in TH ], key=lambda x:x[0]):
    print("Profe:",x," total horas:" , y," asignaturas:",z)

  #print(k,v['m'], "total:",v['total_horas'])
  
  return TH


In [0]:
#{"1ALEN": {"profe": 11}, "1AMAT": {"profe": 9}, "1AING": {"profe": 11}, "1AEFI": {"profe": 15}, "1ANAT": {"profe": 2}, "1ASOC": {"profe": 9}, "1ALIB": {"profe": 16}, "1AREL": {"profe": 4}, "1AART": {"profe": 11}, "1BLEN": {"profe": 6}, "1BMAT": {"profe": 4}, "1BING": {"profe": 11}, "1BEFI": {"profe": 15}, "1BNAT": {"profe": 2}, "1BSOC": {"profe": 4}, "1BLIB": {"profe": 17}, "1BREL": {"profe": 4}, "1BART": {"profe": 4}, "2ALEN": {"profe": 5}, "2AMAT": {"profe": 6}, "2AING": {"profe": 13}, "2AEFI": {"profe": 15}, "2ANAT": {"profe": 8}, "2ASOC": {"profe": 6}, "2ALIB": {"profe": 16}, "2AREL": {"profe": 1}, "2AART": {"profe": 5}, "2BLEN": {"profe": 1}, "2BMAT": {"profe": 5}, "2BING": {"profe": 13}, "2BEFI": {"profe": 15}, "2BNAT": {"profe": 4}, "2BSOC": {"profe": 5}, "2BLIB": {"profe": 17}, "2BREL": {"profe": 1}, "2BART": {"profe": 8}, "3ALEN": {"profe": 12}, "3AMAT": {"profe": 12}, "3AING": {"profe": 10}, "3AEFI": {"profe": 15}, "3ANAT": {"profe": 12}, "3ASOC": {"profe": 5}, "3ALIB": {"profe": 16}, "3AREL": {"profe": 4}, "3AART": {"profe": 4}, "3BLEN": {"profe": 8}, "3BMAT": {"profe": 8}, "3BING": {"profe": 10}, "3BEFI": {"profe": 15}, "3BNAT": {"profe": 5}, "3BSOC": {"profe": 1}, "3BLIB": {"profe": 17}, "3BREL": {"profe": 4}, "3BART": {"profe": 5}, "4ALEN": {"profe": 13}, "4AMAT": {"profe": 6}, "4AING": {"profe": 10}, "4AEFI": {"profe": 14}, "4ANAT": {"profe": 14}, "4ASOC": {"profe": 13}, "4ALIB": {"profe": 17}, "4AREL": {"profe": 1}, "4AART": {"profe": 7}, "4BLEN": {"profe": 1}, "4BMAT": {"profe": 6}, "4BING": {"profe": 13}, "4BEFI": {"profe": 14}, "4BNAT": {"profe": 13}, "4BSOC": {"profe": 10}, "4BLIB": {"profe": 17}, "4BREL": {"profe": 1}, "4BART": {"profe": 1}, "5ALEN": {"profe": 11}, "5AMAT": {"profe": 9}, "5AING": {"profe": 12}, "5AEFI": {"profe": 14}, "5ANAT": {"profe": 2}, "5ASOC": {"profe": 2}, "5ALIB": {"profe": 17}, "5AREL": {"profe": 2}, "5AART": {"profe": 7}, "5BLEN": {"profe": 2}, "5BMAT": {"profe": 14}, "5BING": {"profe": 12}, "5BEFI": {"profe": 14}, "5BNAT": {"profe": 7}, "5BSOC": {"profe": 11}, "5BLIB": {"profe": 17}, "5BREL": {"profe": 2}, "5BART": {"profe": 12}, "6ALEN": {"profe": 9}, "6AMAT": {"profe": 7}, "6AING": {"profe": 10}, "6AEFI": {"profe": 15}, "6ANAT": {"profe": 7}, "6ASOC": {"profe": 7}, "6ALIB": {"profe": 17}, "6AREL": {"profe": 2}, "6AART": {"profe": 7}, "6BLEN": {"profe": 9}, "6BMAT": {"profe": 8}, "6BING": {"profe": 10}, "6BEFI": {"profe": 14}, "6BNAT": {"profe": 8}, "6BSOC": {"profe": 7}, "6BLIB": {"profe": 17}, "6BREL": {"profe": 3}, "6BART": {"profe": 15}}
asignaturas_impartidas_x_profesor(LA_MEJOR_S)

Profe: 1  total horas: 23  asignaturas: ['1AREL', '1AART', '1BREL', '3ALEN', '3AREL', '3AART', '3BLEN', '3BSOC']
Profe: 2  total horas: 23  asignaturas: ['5ASOC', '5AREL', '5BNAT', '5BSOC', '6ALEN', '6ANAT', '6AREL', '6BREL']
Profe: 3  total horas: 23  asignaturas: ['2ASOC', '2AREL', '2BREL', '3BREL', '4AMAT', '4ASOC', '4AREL', '4BREL', '4BART']
Profe: 4  total horas: 5BREL  asignaturas: ['5BREL']
Profe: 5  total horas: 23  asignaturas: ['2ALEN', '2AMAT', '2BSOC', '6ASOC', '6BMAT', '6BART']
Profe: 6  total horas: 23  asignaturas: ['1BMAT', '1BNAT', '1BART', '2BMAT', '3AMAT', '3ANAT']
Profe: 7  total horas: 23  asignaturas: ['1ANAT', '1BLEN', '2BLEN', '2BNAT', '5ANAT', '5AART', '5BART']
Profe: 8  total horas: 23  asignaturas: ['4ANAT', '4AART', '4BMAT', '4BSOC', '5ALEN', '5AMAT']
Profe: 9  total horas: 23  asignaturas: ['1ALEN', '1ASOC', '1BSOC', '6AMAT', '6AART', '6BLEN']
Profe: 10  total horas: 23  asignaturas: ['3AING', '3BART', '4ALEN', '4BING', '5AING', '5BING']
Profe: 11  total ho

[{9: {'m': ['1ALEN', '1ASOC', '1BSOC', '6AMAT', '6AART', '6BLEN'],
   'total_horas': 23,
   'total_materias': 6}},
 {11: {'m': ['1AMAT', '1AING', '1BING', '5BLEN', '5BMAT'],
   'total_horas': 23,
   'total_materias': 5}},
 {14: {'m': ['1AEFI',
    '1BEFI',
    '2AART',
    '2BEFI',
    '3AEFI',
    '3ASOC',
    '3BEFI',
    '3BNAT'],
   'total_horas': 23,
   'total_materias': 8}},
 {7: {'m': ['1ANAT', '1BLEN', '2BLEN', '2BNAT', '5ANAT', '5AART', '5BART'],
   'total_horas': 23,
   'total_materias': 7}},
 {16: {'m': ['1ALIB', '1BLIB', '4BLIB', '5BLIB', '6BLIB'],
   'total_horas': 15,
   'total_materias': 5}},
 {1: {'m': ['1AREL',
    '1AART',
    '1BREL',
    '3ALEN',
    '3AREL',
    '3AART',
    '3BLEN',
    '3BSOC'],
   'total_horas': 23,
   'total_materias': 8}},
 {6: {'m': ['1BMAT', '1BNAT', '1BART', '2BMAT', '3AMAT', '3ANAT'],
   'total_horas': 23,
   'total_materias': 6}},
 {5: {'m': ['2ALEN', '2AMAT', '2BSOC', '6ASOC', '6BMAT', '6BART'],
   'total_horas': 23,
   'total_materias':

In [0]:
#1 solo profe sin el maximo de horas: valor: 1121
_={"1ALEN": {"profe": 11}, "1AMAT": {"profe": 9}, "1AING": {"profe": 11}, "1AEFI": {"profe": 15}, "1ANAT": {"profe": 2}, "1ASOC": {"profe": 9}, "1ALIB": {"profe": 16}, "1AREL": {"profe": 4}, "1AART": {"profe": 11}, "1BLEN": {"profe": 6}, "1BMAT": {"profe": 4}, "1BING": {"profe": 11}, "1BEFI": {"profe": 15}, "1BNAT": {"profe": 2}, "1BSOC": {"profe": 4}, "1BLIB": {"profe": 17}, "1BREL": {"profe": 4}, "1BART": {"profe": 4}, "2ALEN": {"profe": 5}, "2AMAT": {"profe": 6}, "2AING": {"profe": 13}, "2AEFI": {"profe": 15}, "2ANAT": {"profe": 8}, "2ASOC": {"profe": 6}, "2ALIB": {"profe": 16}, "2AREL": {"profe": 1}, "2AART": {"profe": 5}, "2BLEN": {"profe": 1}, "2BMAT": {"profe": 5}, "2BING": {"profe": 13}, "2BEFI": {"profe": 15}, "2BNAT": {"profe": 4}, "2BSOC": {"profe": 5}, "2BLIB": {"profe": 17}, "2BREL": {"profe": 1}, "2BART": {"profe": 8}, "3ALEN": {"profe": 12}, "3AMAT": {"profe": 12}, "3AING": {"profe": 10}, "3AEFI": {"profe": 15}, "3ANAT": {"profe": 12}, "3ASOC": {"profe": 5}, "3ALIB": {"profe": 16}, "3AREL": {"profe": 4}, "3AART": {"profe": 4}, "3BLEN": {"profe": 8}, "3BMAT": {"profe": 8}, "3BING": {"profe": 10}, "3BEFI": {"profe": 15}, "3BNAT": {"profe": 5}, "3BSOC": {"profe": 1}, "3BLIB": {"profe": 17}, "3BREL": {"profe": 4}, "3BART": {"profe": 5}, "4ALEN": {"profe": 13}, "4AMAT": {"profe": 6}, "4AING": {"profe": 10}, "4AEFI": {"profe": 14}, "4ANAT": {"profe": 14}, "4ASOC": {"profe": 13}, "4ALIB": {"profe": 17}, "4AREL": {"profe": 1}, "4AART": {"profe": 7}, "4BLEN": {"profe": 1}, "4BMAT": {"profe": 6}, "4BING": {"profe": 13}, "4BEFI": {"profe": 14}, "4BNAT": {"profe": 13}, "4BSOC": {"profe": 10}, "4BLIB": {"profe": 17}, "4BREL": {"profe": 1}, "4BART": {"profe": 1}, "5ALEN": {"profe": 11}, "5AMAT": {"profe": 9}, "5AING": {"profe": 12}, "5AEFI": {"profe": 14}, "5ANAT": {"profe": 2}, "5ASOC": {"profe": 2}, "5ALIB": {"profe": 17}, "5AREL": {"profe": 2}, "5AART": {"profe": 7}, "5BLEN": {"profe": 2}, "5BMAT": {"profe": 14}, "5BING": {"profe": 12}, "5BEFI": {"profe": 14}, "5BNAT": {"profe": 7}, "5BSOC": {"profe": 11}, "5BLIB": {"profe": 17}, "5BREL": {"profe": 2}, "5BART": {"profe": 12}, "6ALEN": {"profe": 9}, "6AMAT": {"profe": 7}, "6AING": {"profe": 10}, "6AEFI": {"profe": 15}, "6ANAT": {"profe": 7}, "6ASOC": {"profe": 7}, "6ALIB": {"profe": 17}, "6AREL": {"profe": 2}, "6AART": {"profe": 7}, "6BLEN": {"profe": 9}, "6BMAT": {"profe": 8}, "6BING": {"profe": 10}, "6BEFI": {"profe": 14}, "6BNAT": {"profe": 8}, "6BSOC": {"profe": 7}, "6BLIB": {"profe": 17}, "6BREL": {"profe": 3}, "6BART": {"profe": 15}}

#2 profes sin el maximo de horas: valor: 2118.636396103068
_={"1ALEN": {"profe": 9}, "1AMAT": {"profe": 12}, "1AING": {"profe": 12}, "1AEFI": {"profe": 15}, "1ANAT": {"profe": 1}, "1ASOC": {"profe": 10}, "1ALIB": {"profe": 17}, "1AREL": {"profe": 1}, "1AART": {"profe": 6}, "1BLEN": {"profe": 2}, "1BMAT": {"profe": 9}, "1BING": {"profe": 10}, "1BEFI": {"profe": 15}, "1BNAT": {"profe": 1}, "1BSOC": {"profe": 1}, "1BLIB": {"profe": 17}, "1BREL": {"profe": 2}, "1BART": {"profe": 10}, "2ALEN": {"profe": 5}, "2AMAT": {"profe": 3}, "2AING": {"profe": 11}, "2AEFI": {"profe": 15}, "2ANAT": {"profe": 3}, "2ASOC": {"profe": 6}, "2ALIB": {"profe": 16}, "2AREL": {"profe": 2}, "2AART": {"profe": 9}, "2BLEN": {"profe": 6}, "2BMAT": {"profe": 3}, "2BING": {"profe": 11}, "2BEFI": {"profe": 15}, "2BNAT": {"profe": 11}, "2BSOC": {"profe": 5}, "2BLIB": {"profe": 16}, "2BREL": {"profe": 2}, "2BART": {"profe": 3}, "3ALEN": {"profe": 7}, "3AMAT": {"profe": 5}, "3AING": {"profe": 12}, "3AEFI": {"profe": 14}, "3ANAT": {"profe": 2}, "3ASOC": {"profe": 5}, "3ALIB": {"profe": 17}, "3AREL": {"profe": 4}, "3AART": {"profe": 5}, "3BLEN": {"profe": 5}, "3BMAT": {"profe": 3}, "3BING": {"profe": 12}, "3BEFI": {"profe": 14}, "3BNAT": {"profe": 14}, "3BSOC": {"profe": 7}, "3BLIB": {"profe": 17}, "3BREL": {"profe": 4}, "3BART": {"profe": 7}, "4ALEN": {"profe": 8}, "4AMAT": {"profe": 8}, "4AING": {"profe": 11}, "4AEFI": {"profe": 14}, "4ANAT": {"profe": 8}, "4ASOC": {"profe": 6}, "4ALIB": {"profe": 16}, "4AREL": {"profe": 4}, "4AART": {"profe": 6}, "4BLEN": {"profe": 7}, "4BMAT": {"profe": 6}, "4BING": {"profe": 11}, "4BEFI": {"profe": 14}, "4BNAT": {"profe": 6}, "4BSOC": {"profe": 3}, "4BLIB": {"profe": 17}, "4BREL": {"profe": 4}, "4BART": {"profe": 8}, "5ALEN": {"profe": 9}, "5AMAT": {"profe": 2}, "5AING": {"profe": 11}, "5AEFI": {"profe": 14}, "5ANAT": {"profe": 9}, "5ASOC": {"profe": 9}, "5ALIB": {"profe": 16}, "5AREL": {"profe": 2}, "5AART": {"profe": 14}, "5BLEN": {"profe": 10}, "5BMAT": {"profe": 8}, "5BING": {"profe": 10}, "5BEFI": {"profe": 14}, "5BNAT": {"profe": 7}, "5BSOC": {"profe": 7}, "5BLIB": {"profe": 16}, "5BREL": {"profe": 2}, "5BART": {"profe": 7}, "6ALEN": {"profe": 13}, "6AMAT": {"profe": 13}, "6AING": {"profe": 13}, "6AEFI": {"profe": 15}, "6ANAT": {"profe": 8}, "6ASOC": {"profe": 13}, "6ALIB": {"profe": 16}, "6AREL": {"profe": 1}, "6AART": {"profe": 13}, "6BLEN": {"profe": 1}, "6BMAT": {"profe": 10}, "6BING": {"profe": 13}, "6BEFI": {"profe": 15}, "6BNAT": {"profe": 15}, "6BSOC": {"profe": 1}, "6BLIB": {"profe": 17}, "6BREL": {"profe": 1}, "6BART": {"profe": 15}}

#3 profes sin el maximo de horas: valor: 1095
_={"1ALEN": {"profe": 9}, "1AMAT": {"profe": 11}, "1AING": {"profe": 11}, "1AEFI": {"profe": 14}, "1ANAT": {"profe": 7}, "1ASOC": {"profe": 9}, "1ALIB": {"profe": 16}, "1AREL": {"profe": 1}, "1AART": {"profe": 1}, "1BLEN": {"profe": 7}, "1BMAT": {"profe": 6}, "1BING": {"profe": 11}, "1BEFI": {"profe": 14}, "1BNAT": {"profe": 6}, "1BSOC": {"profe": 9}, "1BLIB": {"profe": 16}, "1BREL": {"profe": 1}, "1BART": {"profe": 6}, "2ALEN": {"profe": 5}, "2AMAT": {"profe": 5}, "2AING": {"profe": 13}, "2AEFI": {"profe": 15}, "2ANAT": {"profe": 13}, "2ASOC": {"profe": 3}, "2ALIB": {"profe": 17}, "2AREL": {"profe": 3}, "2AART": {"profe": 14}, "2BLEN": {"profe": 7}, "2BMAT": {"profe": 6}, "2BING": {"profe": 13}, "2BEFI": {"profe": 14}, "2BNAT": {"profe": 7}, "2BSOC": {"profe": 5}, "2BLIB": {"profe": 17}, "2BREL": {"profe": 3}, "2BART": {"profe": 15}, "3ALEN": {"profe": 1}, "3AMAT": {"profe": 6}, "3AING": {"profe": 10}, "3AEFI": {"profe": 14}, "3ANAT": {"profe": 6}, "3ASOC": {"profe": 14}, "3ALIB": {"profe": 17}, "3AREL": {"profe": 1}, "3AART": {"profe": 1}, "3BLEN": {"profe": 1}, "3BMAT": {"profe": 12}, "3BING": {"profe": 12}, "3BEFI": {"profe": 14}, "3BNAT": {"profe": 14}, "3BSOC": {"profe": 1}, "3BLIB": {"profe": 17}, "3BREL": {"profe": 3}, "3BART": {"profe": 10}, "4ALEN": {"profe": 10}, "4AMAT": {"profe": 3}, "4AING": {"profe": 13}, "4AEFI": {"profe": 15}, "4ANAT": {"profe": 8}, "4ASOC": {"profe": 3}, "4ALIB": {"profe": 17}, "4AREL": {"profe": 3}, "4AART": {"profe": 8}, "4BLEN": {"profe": 13}, "4BMAT": {"profe": 8}, "4BING": {"profe": 10}, "4BEFI": {"profe": 15}, "4BNAT": {"profe": 13}, "4BSOC": {"profe": 8}, "4BLIB": {"profe": 16}, "4BREL": {"profe": 3}, "4BART": {"profe": 3}, "5ALEN": {"profe": 8}, "5AMAT": {"profe": 8}, "5AING": {"profe": 10}, "5AEFI": {"profe": 15}, "5ANAT": {"profe": 7}, "5ASOC": {"profe": 2}, "5ALIB": {"profe": 17}, "5AREL": {"profe": 2}, "5AART": {"profe": 7}, "5BLEN": {"profe": 11}, "5BMAT": {"profe": 11}, "5BING": {"profe": 10}, "5BEFI": {"profe": 15}, "5BNAT": {"profe": 2}, "5BSOC": {"profe": 2}, "5BLIB": {"profe": 16}, "5BREL": {"profe": 4}, "5BART": {"profe": 7}, "6ALEN": {"profe": 2}, "6AMAT": {"profe": 9}, "6AING": {"profe": 12}, "6AEFI": {"profe": 15}, "6ANAT": {"profe": 2}, "6ASOC": {"profe": 5}, "6ALIB": {"profe": 17}, "6AREL": {"profe": 2}, "6AART": {"profe": 9}, "6BLEN": {"profe": 9}, "6BMAT": {"profe": 5}, "6BING": {"profe": 12}, "6BEFI": {"profe": 15}, "6BNAT": {"profe": 12}, "6BSOC": {"profe": 12}, "6BLIB": {"profe": 16}, "6BREL": {"profe": 2}, "6BART": {"profe": 5}} 
asignaturas_impartidas_x_profesor(_)
evalua_solucion_profesores(_,PARAMETROS)

Profe: 1  total horas: 23  asignaturas: ['1AREL', '1AART', '1BREL', '3ALEN', '3AREL', '3AART', '3BLEN', '3BSOC']
Profe: 2  total horas: 23  asignaturas: ['5ASOC', '5AREL', '5BNAT', '5BSOC', '6ALEN', '6ANAT', '6AREL', '6BREL']
Profe: 3  total horas: 23  asignaturas: ['2ASOC', '2AREL', '2BREL', '3BREL', '4AMAT', '4ASOC', '4AREL', '4BREL', '4BART']
Profe: 4  total horas: 5BREL  asignaturas: ['5BREL']
Profe: 5  total horas: 23  asignaturas: ['2ALEN', '2AMAT', '2BSOC', '6ASOC', '6BMAT', '6BART']
Profe: 6  total horas: 23  asignaturas: ['1BMAT', '1BNAT', '1BART', '2BMAT', '3AMAT', '3ANAT']
Profe: 7  total horas: 23  asignaturas: ['1ANAT', '1BLEN', '2BLEN', '2BNAT', '5ANAT', '5AART', '5BART']
Profe: 8  total horas: 23  asignaturas: ['4ANAT', '4AART', '4BMAT', '4BSOC', '5ALEN', '5AMAT']
Profe: 9  total horas: 23  asignaturas: ['1ALEN', '1ASOC', '1BSOC', '6AMAT', '6AART', '6BLEN']
Profe: 10  total horas: 23  asignaturas: ['3AING', '3BART', '4ALEN', '4BING', '5AING', '5BING']
Profe: 11  total ho

1095

In [0]:
#Se observa que en la primera fase se pueden ajustar algunas asignaciones manualmente según convenga
#Con los criterios se consigue una solucion con el menor numero de profesores sin jornada completa y con la mejora homogeneidad entre las horas de estos

#2ª FASE. Asignar el horario sobre la solución obtenida para las materias

#MERJORA. Hay dias que aparecen con 2 o 3 horas libre. Se puede mejorar buscando que no haya más de una hora al dia libre

#Genera una solucion para los horarios partiendo de una solucion para profesores asignados
def genera_solucion_horarios(SOLUCION_PROFESORES, PARAMETROS):
  
  #Se asume que se eligen dias de 1 a 5

  SOLUCION = copy.deepcopy(SOLUCION_PROFESORES)
 
  
  for c in PARAMETROS['CURSOS']:
    for l in PARAMETROS['LETRAS']:
      #print(c,l)
      total_asignadas_x_dia=[0]*5

      dias_ocupados = {0:0,1:0,2:0,3:0,4:0}

      #Recorre cada materia con sus horas a la semana
      for m,h in  PARAMETROS['MATERIAS'].items()  :
        #print("\t",m,h)
        dias = []   #Guarda los dias que ya se han asignado para no repetir
        dias_completos=[]   #Guarda los dias que se ha detectado que están completos para no elegirlos
        while (len(dias) < h):
          
          #Elige un dia de los no elegidos. Es necesario elegir entre los dias dias que mas horas disponibles tengan 
          # porque puede ocurrir que para la ultima elección de 2 horas solo quede un dia con dos horas libres
          
          #dia = random.choice(  list(set(range(5)) - set(dias) - set(dias_completos) )  )
          dia = random.choice(list(set([k for k,v in dias_ocupados.items() if v == min([i for i in dias_ocupados.values()]) ]) -   set(dias) ))



          #PENDIENTE. Hacer la asignacion de los dias que menos horas asignadas tiene
          #dia = random.choice([indx for indx, x in list(set(range(5)) - set(dias)) if x ==  ] 

          #Elige una hora para ese dia 
          if not 'horas' in SOLUCION[str(c)+str(l)+m] :
            SOLUCION[str(c)+str(l)+m]['horas'] = []

          ha = horas_asignadas(SOLUCION, c, l,  dia,  PARAMETROS)            

          if len(list(set(list(range(PARAMETROS['HORAS'])))-ha) ) == 0:
            #print("\t\t","No hay horas libres para el dia ", dia )
            dias_completos.append(dia ) 
            
            #Ya no debería entrar por aqui
            if len(dias) + len(dias_completos) == 5:
              print("\t\tdias no disponibles:", dias,"\tdias completos:", dias_completos, "\tdias ocupados:",dias_ocupados)
              imprime_horarios(SOLUCION,PARAMETROS)
              print("****No hay DIAS libres para el dia ", dia)
              return  
             

          else:
            #print(m, "Para el dia " ,dia , "asignadas:" ,ha, " elige entre " , list(set(list(range(PARAMETROS['HORAS'])))-ha) , end="")
            hora = random.choice( list(set(list(range(PARAMETROS['HORAS'])))-ha)  )
            #print(" hora elegida:" ,hora,"\n")
            dias.append(dia )
            dias_ocupados[dia] =dias_ocupados[dia]+1
            #total_asignadas_x_dia = [ 1+total_asignadas_x_dia[dia] if indx ==dia else x  for indx,x in enumerate(total_asignadas_x_dia)]
            SOLUCION[str(c)+str(l)+m]['dias'] = list(dias)
            SOLUCION[str(c)+str(l)+m]['horas'].append(hora )
            #print("\t\tSe asigna dia" ,dia ," y hora:", hora)
          #print('total_asignadas_x_dia:', total_asignadas_x_dia)


 
  return  SOLUCION 

#Devuelve las horas ya asignadas a un curso/letra
def horas_asignadas(SOLUCION,CURSO, LETRA, DIA, PARAMETROS):
  return  set(reduce(lambda c, x: c + x, [ [v['horas'][i] for i in range( len(v['horas']) ) if v['dias'][i] == DIA ] if 'dias' in v else [] for k,v in SOLUCION.items() if k[0:2] == str(CURSO)+str(LETRA) ]))







In [0]:
#Devuelve un objeto que por curso(curso+letra) contiene un array con dias/horas y la asignatura
# para imprimir correctamente el horario 
def convierte_a_horarios(S,PARAMETROS):
  #Lista con todos los cursos y letras 1A, 1A, 2B...
  CURSOS_LETRAS = [str(c)+str(l) for c in PARAMETROS['CURSOS'] for l in PARAMETROS['LETRAS'] ]
  
  #print(CURSOS_LETRAS)

  #Inicializa la tabla de horarios
  HORARIOS = {k:np.array([[np.array("")]*6]*5,dtype=object) for k in CURSOS_LETRAS }

  #Actualiza los datos de horarios
  for k,v in S.items()  :

    #print( k[2:5])
    #print(k,v)
    #print("\t", v['dias'], v['horas'] )
    if 'dias' in v:
      for i in range(len(v['dias'])):
        #print("\t\t",v['dias'][i], v['horas'][i], k,v )
        if  not isinstance(HORARIOS[k[0:2]][v['dias'][i]][v['horas'][i]], list)  : 
          HORARIOS[k[0:2]][v['dias'][i]][v['horas'][i]] = [k[2:5]]
        else:
          HORARIOS[k[0:2]][v['dias'][i]][v['horas'][i]] = np.array(HORARIOS[k[0:2]][v['dias'][i]][v['horas'][i]] + [k[2:5]]   )
  
  return HORARIOS
 

def imprime_horarios(S,PARAMETROS):
  HORARIOS = convierte_a_horarios(S,PARAMETROS)
  for c in HORARIOS :
    print("\n\n", c, "\n----------------------------------------------------------------------------------------------------")
    print(   "  L       \tM       \tX       \tJ       \tV       ")
    print(    "----------------------------------------------------------------------------------------------------")

 
 
    for h in range(PARAMETROS['HORAS']):
      print('\t')
      for d  in range(5):
        try:
          profe=   "("+str(S[c+str(HORARIOS[c][d][h][0])]['profe']).rjust(2)+")" if HORARIOS[c][d][h] else "(  )" 
          print(   HORARIOS[c][d][h][0]+profe if HORARIOS[c][d][h]  else "---"+profe , '\t' ,end=""  )
        except :
          print(   "/".join(HORARIOS[c][d][h] )  , '\t' ,end="" )
    

      print()
 
    print()
    #return  
  return
 
 


In [0]:
#Analiza una solucion para encotrar las horas repetidas, ocupadas y libres de cada profesor
def analiza_solucion(S,PARAMETROS):
  #Dias y horas de cada profesor
  REPETIDAS = {}
  OCUPADAS  = {}
  LIBRES    = {}
  for p,asig in PARAMETROS['PROFESORES'].items():
    OCUPADAS[p] = list(chain(*[ list(map(lambda x:str(x[0])+ "-" +str(x[1]) , list(zip(v['dias'],v['horas']) )))   for m,v in S.items() if v['profe'] ==p and m[2:5] != 'LIB'     ]))
    REPETIDAS[p] = {x:OCUPADAS[p].count(x) for x in OCUPADAS[p] if OCUPADAS[p].count(x) >1}
 
    #print("Profe:", p ,"tiene ", len(PP) - len(set(PP)) , {x:PP.count(x) for x in a if PP.count(x) >1} , "\t\t", PP )


  #Busca las horas libres para cada profesor
  for p,asig in PARAMETROS['PROFESORES'].items():
    LIBRES[p] = []
    for d in range(5):
      for h in range(PARAMETROS['HORAS']):
        if str(d) + "-" +  str(h) not in OCUPADAS[p]:
          LIBRES[p].append(str(d) + "-" +  str(h))

  #print("REPETIDAS", json.dumps(REPETIDAS))
  #print("OCUPADAS",json.dumps(OCUPADAS))
  #print("LIBRES",json.dumps(LIBRES))

  return {"REPETIDAS":  REPETIDAS , "OCUPADAS": OCUPADAS , "LIBRES": LIBRES  }


#Busca profes libres para un dia-hora
def busca_profes_libres(S, DIA_HORA, PARAMETROS):
  return [p for p,dh in analiza_solucion(S,PARAMETROS)['LIBRES'].items() if DIA_HORA in dh  ]

#Busca la asigantura que imparte un profesor a un dia y hora dada
def busca_materia(S,PROFESOR, DIA_HORA, PARAMETROS):
  #DIA_HORA en formato d-h

  return [ k for k,d in S.items() if PROFESOR == d['profe'] and DIA_HORA in [str(d['dias'][i]) + '-' +str(d['horas'][i])  for i in range(len(d['dias'])) ]    ]

#Devuelve curso/materia que se imparte un profesor en un dia y hora
def get_materia(SOLUCION=[], profe=0, dia=0, hora=0, PARAMETROS=PARAMETROS):
  return [ m for m,dh in [ (k,  list(map(lambda x:str(x[0]) + "-" + str(x[1]), list(zip(v['dias'],v['horas']))) )  )  for k,v in SOLUCION.items() if v['profe']  == profe]  if  str(dia)+"-"+str(hora) in dh ]
 

In [0]:
#Evalua la poblacion teniendo en cuenta los horarios asignados
def evalua_solucion_horarios(SOLUCION_ORIGINAL, PARAMETROS , imprime=0):
    W1 = 1000  #Peso para penalizar por cada hora en que un profesor repite dia y hora
    W2  =100   #Peso por cada profesor que no completa el maximo de horas
    W3 = 10    #Peso por cada hora libre que no es la ultima o la primera del dia
    W4 = 1     #Peso por la variabilidad de las horas libres que no sean al principio y al final del dias
    VALOR = 0
    
    #Elimina las asignaturas **LIB que en realidad son horas libres para no evaluarlas
    SOLUCION = { k:v for k,v in SOLUCION_ORIGINAL.items() if k[2:5] != 'LIB'}

    SUM_HORAS_PROFES = sum_horas_profes(SOLUCION, PARAMETROS)
    #Penaliza(W1) cada hora que un profesor se pasa del maximo de horas
    for x in SUM_HORAS_PROFES:
      if x['horas'] > PARAMETROS['MAX_HORAS_X_PROFESOR']:
        VALOR += W1*(x['horas'] - PARAMETROS['MAX_HORAS_X_PROFESOR'])


    #Penaliza(W1) cada hora en que un profesor repite dia y hora
    ####################################################################
    #  Obtiene las coincidencias para cada profesor
    PROF = {} #Contiene las asignaturas de cada profe
    for c,p in SOLUCION.items():
      if p['profe'] in PROF:
        PROF[p['profe']].append(c)
      else:
        PROF[p['profe']] = [c]
    #Obtiene la lista de las (dias,horas) que da clase cada profesor
    HORAS_PROFE = [ list(map(lambda x :  list(zip(SOLUCION[x]['dias'],SOLUCION[x]['horas'])),M)) for P,M in PROF.items() ]
    for HP in HORAS_PROFE:
      temp = [ str(list(j)[0])+ "-"+str(list(j)[1]) for i in HP for j in i  ]
      #print(temp, "\n", "coincidencias:", len(temp) - len(set(temp)), "\n")
      VALOR += W1*(len(temp) - len(set(temp)) )

    #Penaliza por profesores que no completan las horas maximas
    PROFES_NO_COMPLETA=[]
    #SUM_HORAS_PROFES  = list(map(lambda x:{"profe":x[0],"horas": sum( map(lambda y:PARAMETROS['MATERIAS'][y[2:5]] , x[1]) ), "s":x[1] } ,PROF.items() )   )
    for x in SUM_HORAS_PROFES:
      if x['horas'] < PARAMETROS['MAX_HORAS_X_PROFESOR'] and x['horas'] > 0:
        VALOR += W2
        PROFES_NO_COMPLETA.append(x['horas'])


    ANALIZA = analiza_solucion(SOLUCION, PARAMETROS)["LIBRES"].items()
    #Añade horas libres de profesores con peso W2 que no estan al inicio o al final 
    VALOR += sum([  len([x[2] for x in v if int(x[2])*W3  !=  PARAMETROS['HORAS']-1  and int(x[2])  !=  0  ] ) for k,v in ANALIZA ])

    #Horas libres al principio o final del dia de los profesores. Trata de uniformizar lo mas posible estas horas libres
    VALOR += W4*statistics.stdev([  len([x for x in v if x[2] == '0' or x[2] == '5'])   for k,v in ANALIZA if k in [k for k,v in PARAMETROS['PROFESORES'].items() if 'LIB' not in v ] ])


    #PENDIENTE. Añade peso por la variabilidad de horas libres que no sean al principio y al final
    # o al reves beneficia por la poca variabilida de horas libres al principio y al final del dia.
 

    return VALOR
  




In [0]:
#Evolutivo
#Para una buena solución en la que aun hay repeticion de clases para profesores, 
#   se prueba mutaciones sobre ella intercambiando horarios y profesores que repiten hora.
def mutacion_profesores_v1(SOLUCION, PARAMETROS , modo="N/A" ):
  N_MAX_MUTACIONES = 15
  SOLUCION_COPIA = copy.deepcopy(SOLUCION)
  
  #Elige el nº aleatorio de cambios
  n_cambios = random.choice(range(1,N_MAX_MUTACIONES+1))
  SELECT1=set()
  SELECT2=set()
  for i in range(n_cambios):
    materia_curso1  = select(set(SOLUCION.keys())-SELECT1-SELECT2,1)[0]

    #Elige la misma materia pero de otro curso/letra
    materia_curso2 =""
    while materia_curso2 == materia_curso1 or materia_curso2 == "":
      materia_curso2 = str(select(PARAMETROS['CURSOS'],1)[0]) + select(PARAMETROS['LETRAS'],1)[0] + materia_curso1[2:5]
      #print(materia_curso1 ,materia_curso2)

    profe1 =  SOLUCION[ materia_curso1 ]['profe']
    profe2 =  SOLUCION[ materia_curso2 ]['profe']
    
    SOLUCION_COPIA[ materia_curso1 ]['profe'] = profe2
    SOLUCION_COPIA[ materia_curso2 ]['profe'] = profe1
    
    #print(materia_curso1,materia_curso2,profe1,profe2)

  return SOLUCION_COPIA

#Mutacion de profesores dirigida a los profesores que tienen horas repetidas
#V2 se dirige mejor la busqueda asignando al profesor que más horas libres tenga
def mutacion_profesores(S_INPUT , PARAMETROS, modo="max_horas"  ):

  SOLUCION  = copy.deepcopy(S_INPUT)

  ANALIZA_SOLUCION =   analiza_solucion(SOLUCION,PARAMETROS)
  REPETIDAS  =[ (k,v) for k,v in ANALIZA_SOLUCION["REPETIDAS"].items() if v != {}  ]
  #print("Repetidas:" , REPETIDAS)

  #PENDIENTE. Si no hay repetidas hacer otro intercambio para buscar la mejora
  #Si no hay repetidas no hace mutaciones
  if len(REPETIDAS) ==0:
    return SOLUCION

  p,hs=  random.choice([ (k,v) for k,v in ANALIZA_SOLUCION["REPETIDAS"].items() if v != {}  ] )
  hd= random.choice(list(hs))
  materia_desde = random.choice(busca_materia(SOLUCION, p,hd, PARAMETROS))

  profe_desde = SOLUCION[materia_desde]['profe']

  

  #Busca el profesor que menos horas tenga asignadas
  #print( [ {'p':x[0],'total':len(x[1]) } for x in ANALIZA_SOLUCION["LIBRES"].items() ]) 
  #return  sorted([ {'p':x[0],'total':len(x[1]) } for x in ANALIZA_SOLUCION["LIBRES"].items() ] , key=lambda x:x['total'] , reverse=True )
  try:
    if modo == 'max_horas': 
      profe_hasta = sorted([ {'p':x[0],'total':len(x[1]) } for x in ANALIZA_SOLUCION["OCUPADAS"].items() if  len(x[1]) == PARAMETROS['MAX_HORAS_X_PROFESOR'] and x[0] != profe_desde and materia_desde[2:5] in PARAMETROS['PROFESORES'][x[0]] ]  , key=lambda x:x['total'] , reverse=True )[0]['p']
      #Elige el que mas horas disponibles tienen
    else:
      #print("Mutacion por no_max_horas")
      #Elige entre los que tienen maxima ocupacion para que no se reduzca el nº de profesores con maxima ocupacion
      #Es posible que no converga a una solución valida(sin profesores con horas repetidas)
      #Elige entre el 25% de los profesores con menos horas
      #profe_hasta = sorted([ {'p':x[0],'total':len(x[1]) } for x in ANALIZA_SOLUCION["LIBRES"].items() if x[0] != profe_desde and materia_desde[2:5] in PARAMETROS['PROFESORES'][x[0]] ]  , key=lambda x:x['total'] , reverse=True )[0]['p']
      profe_hasta, materias_hasta = random.choice(list(filter(lambda x:x[1]!=[] ,[(p, [m for m,d in SOLUCION.items() if d['profe'] == p and  PARAMETROS['MATERIAS'][m[2:5]] == PARAMETROS['MATERIAS'][materia_desde[2:5]] ] )  for  p,v in analiza_solucion(SOLUCION,PARAMETROS)['OCUPADAS'].items() if p!=profe_desde and 'LIB' not in PARAMETROS['PROFESORES'][p] and len(v) == PARAMETROS['MAX_HORAS_X_PROFESOR'] ])))

      #Elige una materia del profesor hasta si hay disponibles entre las mismas asignaturas.
      #PENDIENTE. Se puede mejorar entre las asignaturas que tengan igual de horas o menos para no asignar mas horas del máximo
    try:
      #print("Candidatas:", [k for k,v in SOLUCION.items() if v['profe'] == profe_hasta and PARAMETROS['MATERIAS'][k[2:5]] <= PARAMETROS['MATERIAS'][materia_desde[2:5]]    ])
      
      #Elige entre las materias que tengan menos horas que materias desde
      materia_hasta = random.choice(materias_hasta)
      #print("Solucion antes:" ,SOLUCION)
      SOLUCION[materia_desde]['profe'] = profe_hasta
      SOLUCION[materia_hasta]['profe'] = profe_desde
      #print("\tCambia en ",materia_desde, " " , profe_desde, " por ", profe_hasta, " en materia: " , materia_hasta )
      #print("Solucion despues:" ,SOLUCION)
    except:
      #No encuentra una materia a asignar 
      None


 
  except:
    None 
  
  return SOLUCION

#Se genera una mutacion entre los horarios
# Se eligen al azar N asignaturas y un dia y se intercambian las horas
def mutacion_horarios(S_INPUT , PARAMETROS  ):
  N_CAMBIOS = 1 

  SOLUCION = copy.deepcopy(S_INPUT)

  i = 0
  while i<N_CAMBIOS:
    i+=1
 
    #Elige una meteria que esté repetida
    materias=[]
    repetidas = [ k for k,v in analiza_solucion(SOLUCION,PARAMETROS)["REPETIDAS"].items() if v != {}  ]
    if len(repetidas) > 0:
      materias = repetidas
    else:
      #Si no hay repetidas obtiene otra cualquiera
      materias = [x for x in SOLUCION if x[2:5] != 'LIB']
 
    materia_desde = random.choice([x for x in SOLUCION if x[2:5] != 'LIB'])
    indx_desde,dia_desde=random.choice([  (indx,x)  for indx,x in enumerate(SOLUCION[materia_desde]['dias']) ] )
    hora_desde=SOLUCION[materia_desde]['horas'][indx_desde]

    materia_hasta= random.choice([m for m  in SOLUCION if m[2:5] != 'LIB' and m!=materia_desde and PARAMETROS['MATERIAS'][m[2:5]] == PARAMETROS['MATERIAS'][materia_desde[2:5]]]    )
    indx_hasta,dia_hasta=random.choice([  (indx,x)  for indx,x in enumerate(SOLUCION[materia_hasta]['dias'])   if x != materia_desde ] )
    hora_hasta=SOLUCION[materia_hasta]['horas'][indx_hasta]

    SOLUCION[materia_desde]['dias'][indx_desde],SOLUCION[materia_hasta]['dias'][indx_hasta] = dia_hasta,dia_desde
    SOLUCION[materia_desde]['horas'][indx_desde],SOLUCION[materia_hasta]['horas'][indx_hasta] = hora_hasta , hora_desde
    
    #if  max([ list(x.values())[0]['total_horas']   for  x in  asignaturas_impartidas_x_profesor(S3)     ] ) >  23:
    if  False:
      print("Antes")
      print(materia_desde,SOLUCION[materia_desde])
      print(materia_hasta,SOLUCION[materia_hasta])
      print("\n")


      print("Despues")
      print(materia_desde,SOLUCION[materia_desde])
      print(materia_hasta,SOLUCION[materia_hasta])

  return SOLUCION


#Se genera una mutacion entre los horarios
# Se eligen al azar N asignaturas y un dia y se intercambian las horas
def mutacion_horarios_v1(S_INPUT , PARAMETROS  ):
  N_CAMBIOS = 1 

  SOLUCION = copy.deepcopy(S_INPUT)

  i = 0
  while i<N_CAMBIOS:
    i+=1

    #Se elige una asignatura al azar
    # materia_desde = random.choice( [k for k,v in SOLUCION.items() if k[2:5] != 'LIB' ])

    #Elige un dia al azar
    #indx_desde,dia =  random.choice([(indx ,d) for indx ,d in enumerate(SOLUCION[materia_desde]['dias']) ] )

 
    #Elige una meteria que esté repetida
    materias=[]
    repetidas = [ (k,v) for k,v in analiza_solucion(SOLUCION,PARAMETROS)["REPETIDAS"].items() if v != {}  ]
    if len(repetidas) > 0:
      materias = repetidas
    else:
      #Si no hay repetidas obtiene otra cualquiera
      materias =[ (v['profe'],set(map(lambda x:str(x[0])+"-"+str(x[1]), list(zip(v['dias'], v['horas'])) ))) for k,v in SOLUCION.items() if k[2:5] != 'LIB' ]
      
    p,hs=  random.choice( materias)
    hd= random.choice(list(hs))
 

    materia_desde = random.choice(busca_materia(SOLUCION, p,hd, PARAMETROS))
    dia  = hd[0]

 
    #Busca el indice donde está la hora a intercambiar
    #indx_desde = [v[0] for v in [(indx ,d) for indx ,d in enumerate(SOLUCION[materia_desde]['dias'])    ] if v[1] == dia ][0]
    
    #print(dia , materia_desde,SOLUCION[materia_desde])

    indx_desde =  [v for v in [(indx ,d) for indx ,d in enumerate(SOLUCION[materia_desde]['dias'])    ] if v[1] == int(dia )][0][0]
    hora_desde = SOLUCION[materia_desde]['horas'][indx_desde]

    #print(  "dia :", dia ,"hora:",hora_desde,"indx:",indx_desde)

 

    #Elige otra asignatura para ese dia 
    #PENDIENTE.Mejora: intercambiar con otra materia de otro dia que tenga las mismas horas
    materia_hasta = random.choice(  [   k  for k,v in SOLUCION.items() if k[2:5] != 'LIB' and k != materia_desde and k[0:2] == materia_desde[0:2] and int(dia) in v['dias']   ]   )
    
    
    #print(materia_hasta, SOLUCION[materia_hasta])
    #print(materia_hasta)

    #Busca la hora que se imparte la asignatura de destino
    indx_hasta = [v[0] for v in [(indx_hasta,d) for indx_hasta,d in enumerate(SOLUCION[materia_hasta]['dias'])    ] if v[1] == int(dia)][0]
    hora_hasta =  SOLUCION[materia_hasta]['horas'][indx_hasta]

    SOLUCION[materia_desde]['horas'][indx_desde] = hora_hasta 
    SOLUCION[materia_hasta]['horas'][indx_hasta] = hora_desde

    #if  max([ list(x.values())[0]['total_horas']   for  x in  asignaturas_impartidas_x_profesor(S3)     ] ) >  23:
    if  False:
      print("Antes")
      print(materia_desde,SOLUCION[materia_desde])
      print(materia_hasta,SOLUCION[materia_hasta])
      print("\n")


      print("Despues")
      print(materia_desde,SOLUCION[materia_desde])
      print(materia_hasta,SOLUCION[materia_hasta])

  return SOLUCION


def mutacion_horarios_v2(S_INPUT , PARAMETROS  ):
  N_CAMBIOS = 1

  SOLUCION_RET = copy.deepcopy(S_INPUT)
  

  i = 0
  while i<N_CAMBIOS:
    i+=1

    #Elige una meteria que esté repetida
    p,hs=  random.choice([ (k,v) for k,v in analiza_solucion(S_INPUT,PARAMETROS)["REPETIDAS"].items() if v != {}  ] )
    hd= random.choice(list(hs))
    materia_desde = random.choice(busca_materia(S_INPUT, p,hd, PARAMETROS))
    dia  = hd[0]
    #print(p,hs,hd,materia_desde , dia )
    #print(dia , materia_desde,SOLUCION[materia_desde])

    indx_desde =  [v for v in [(indx ,d) for indx ,d in enumerate(S_INPUT[materia_desde]['dias'])    ] if v[1] == int(dia )][0][0]
    hora_desde = S_INPUT[materia_desde]['horas'][indx_desde]

 
    #print(materia_desde, SOLUCION[materia_desde])
    #print(  "dia :", dia ,"hora:",hora_desde,"indx:",indx_desde)

    #Fija el valor de la solucion actual
    # Probará si intercambiando con cualquiera de las otras asignaturas del dia mejora
    VALOR  = evalua_solucion_horarios(S_INPUT, PARAMETROS)

    #Recorre las asignaturas de ese dia para intercambiarlas
    for materia_hasta in [   k  for k,v in S_INPUT.items() if k[2:5] != 'LIB' and k != materia_desde and k[0:2] == materia_desde[0:2] and int(dia) in v['dias']   ]  :
      SOLUCION = copy.deepcopy(S_INPUT)
      #print(materia_hasta, SOLUCION[materia_hasta])
      #print(materia_hasta)

      #Busca la hora que se imparte la asignatura de destino
      indx_hasta = [v[0] for v in [(indx_hasta,d) for indx_hasta,d in enumerate(SOLUCION[materia_hasta]['dias'])    ] if v[1] == int(dia)][0]
      hora_hasta =  SOLUCION[materia_hasta]['horas'][indx_hasta]

      #print("Antes")
      #print(materia_desde,SOLUCION[materia_desde])
      #print(materia_hasta,SOLUCION[materia_hasta])
      #print("\n")

      SOLUCION[materia_desde]['horas'][indx_desde] = hora_hasta 
      SOLUCION[materia_hasta]['horas'][indx_hasta] = hora_desde
      #print("Despues")
      #print(materia_desde,SOLUCION[materia_desde])
      #print(materia_hasta,SOLUCION[materia_hasta])
      VALOR_TMP = evalua_solucion_horarios(SOLUCION, PARAMETROS)
      if  VALOR_TMP < VALOR:
        VALOR = VALOR_TMP
        SOLUCION_RET = copy.deepcopy(SOLUCION)  
        #print("****Encontrada mejor opcion!!!***")       

  return SOLUCION_RET






#genera_solucion_horarios(SOLUCION_PROFESORES, PARAMETROS)
#mejor_solucion_local( S2, PARAMETROS  ) 
  
def main_evolutivo(SOLUCION=[] , PARAMETROS=PARAMETROS, N_POBLACION=N_POBLACION , modo='max_horas' ):
  #SOLUCION = Es la solucion inicial de partida conteniendo la asignacion de materias a los profesores
  #PARAMETROS = PARAMETROS del centro, materias, profeore, etc
  #N_POBLACION = Tamaño de la POBLACION
  #modo = modo en el que se realiza la mutacion de profesores: max_horas = se elige como destino los que tienen el maximo de horas
  #                                                            no_max_horas = se elige como destino los que no tienen el maximo de horas
  #   Este parametro permite ejecutar el algoritmo en dos fases, 
  #      en la 1ª al llamarlo con el modo max_horas mantiene el requisito de mantener el mayor numero posible de profesores con el maximo de horas
  #      Es muy probable que no se pueda encontrar la solución(sin horas repetidas para los profesores) para la distribucion de la solucion inicial
  #      Entonces se ejecuta el segundo modo(no_max_horas) para buscar entre los profesores que no tienen el maximo de horas asignadas.

  #print("Valor inicial", evalua_solucion_horarios(SOLUCION, PARAMETROS),SOLUCION)

  #POBLACION = [genera_solucion_horarios(SOLUCION, PARAMETROS  ) for i in range(N_POBLACION) ]
  POBLACION =    [ mutacion_horarios(SOLUCION, PARAMETROS  ) for x in  range(N_POBLACION) ]

  MEJOR_VALOR = 100000000
  MEJOR_SOLUCION = {}

  CRITERIO_PARADA = False

  iteracion = 0
  #while iteracion < 1000:
  while CRITERIO_PARADA == False     :
    iteracion +=1

    #Ordena la poblacion y se queda con los mejor valorados. MEJORA.Elegir otro metodo para favorecer aleatoriamente a peores(ruleta)
    ORDENACION= []
    ORDENACION =  list(map(lambda x: {"v":evalua_solucion_horarios(x, PARAMETROS),'s':x} ,POBLACION) ) 
    ORDENACION.sort(key=lambda x: x['v'])

    

 
    if iteracion/1  == iteracion//1 :
      print(iteracion,"#", "Mejor solucion:", ORDENACION[0]['v'], "Peor solucion:", ORDENACION[N_POBLACION-1]['v'], ORDENACION[0]['s'])
      print( "\t", [x['v'] for x in ORDENACION] ,"\n" )
      
    MEJOR_VALOR = ORDENACION[0]['v']
    MEJOR_SOLUCION = ORDENACION[0]['s']
    
    #Se queda con los mejores y se añaden mutaciones por horarios y por profesores
    #PENDIENTE. Probar otros operadores de seleccion. Por ejemplo quedarse con el 50% de los mejores y el resto al azar
    POBLACION = []
    POBLACION =  list(map(lambda x:x['s'],ORDENACION[0:N_POBLACION]))  
      
    #select(list(map(lambda x:x['s'],ORDENACION[N_POBLACION//2:])) , N_POBLACION//2)

    #Añade poblacion por mutaciones de horas
    POBLACION = copy.deepcopy(POBLACION) + copy.deepcopy(list(map(lambda x:mutacion_horarios(x['s'], PARAMETROS  ),ORDENACION[0:N_POBLACION])))


    #Añade poblacion por mutaciones de horas y profesores
    #MEJORA. Seria deseable no ejecutar mutaciones sobre las asignaciones de los profesores para que pued mantenerse un hipotetica asignacion inicial manual.
    #  probar con mutaciones de horas no solo intercambiando horas del mismo dia sino tambien con dias diferentes
    #POBLACION = copy.deepcopy(POBLACION) + copy.deepcopy(list(map(lambda x:mutacion_profesores(x , PARAMETROS , modo=modo ),POBLACION))) 

    #No es necesario aplicar la mejor_solucion_local. El proceso converge más rapidamente y no hace falta
    #POBLACION = list(map( lambda x : mejor_solucion_local( x, PARAMETROS  ) , POBLACION))

    #Añade a la POBLACION una mutacion por cada individuo
    #POBLACION = list(map(lambda x:x, POBLACION)) + [ mutacion_horarios(x,PARAMETROS) for x in  POBLACION ]  
    #POBLACION = list(map(lambda x:x, POBLACION)) + [ mutacion_horarios(x, PARAMETROS  ) for x in  POBLACION ]

    #Si la mitad de la población tiene el mismo valor y es menor que 1000 se termina
    #len(set(list(map(lambda x:x['v'] , ORDENACION[0:N_POBLACION//2])))) == 1
    #Si el modo es max_horas se para si la mitad de la poblacion tiene el mismo valor
    #Si el modo es no_max_horas se para en la iteracion 150 siempre que el valor sea menor que 1000
    if (MEJOR_VALOR < 3000 and iteracion > 50 and modo=="no_max_horas") or (modo=="max_horas" and len(set(list(map(lambda x:x['v'] , ORDENACION[0:N_POBLACION//2])))) == 1) :
      CRITERIO_PARADA = True

  return MEJOR_SOLUCION
#mutacion_profesores(S3, PARAMETROS  ) 

#main_evolutivo(S3 , PARAMETROS, N_POBLACION  )



LA_MEJOR = {'1ALEN': {'profe': 5, 'horas': [5, 2, 2, 0, 5], 'dias': [3, 0, 1, 4, 2]}, '1AMAT': {'profe': 6, 'horas': [4, 4, 4, 3, 1], 'dias': [1, 3, 0, 2, 4]}, '1AING': {'profe': 12, 'horas': [2, 3, 5, 0], 'dias': [4, 0, 1, 2]}, '1AEFI': {'profe': 10, 'horas': [3, 3, 0], 'dias': [3, 4, 1]}, '1ANAT': {'profe': 15, 'horas': [2, 4, 0], 'dias': [3, 2, 0]}, '1ASOC': {'profe': 11, 'horas': [1, 1, 2], 'dias': [3, 1, 2]}, '1ALIB': {'profe': 17, 'horas': [5, 5, 0], 'dias': [4, 0, 3]}, '1AREL': {'profe': 3, 'horas': [4, 3], 'dias': [4, 1]}, '1AART': {'profe': 9, 'horas': [1, 1], 'dias': [2, 0]}, '1BLEN': {'profe': 2, 'horas': [4, 4, 5, 2, 4], 'dias': [4, 0, 2, 1, 3]}, '1BMAT': {'profe': 9, 'horas': [2, 3, 0, 5, 4], 'dias': [4, 1, 0, 3, 2]}, '1BING': {'profe': 10, 'horas': [0, 1, 2, 1], 'dias': [2, 1, 3, 4]}, '1BEFI': {'profe': 15, 'horas': [5, 0, 5], 'dias': [0, 4, 1]}, '1BNAT': {'profe': 8, 'horas': [3, 2, 3], 'dias': [2, 0, 3]}, '1BSOC': {'profe': 8, 'horas': [1, 1, 0], 'dias': [0, 2, 3]}, '1BLIB': {'profe': 16, 'horas': [3, 4, 2], 'dias': [4, 1, 2]}, '1BREL': {'profe': 3, 'horas': [5, 0], 'dias': [4, 1]}, '1BART': {'profe': 6, 'horas': [1, 3], 'dias': [3, 0]}, '2ALEN': {'profe': 9, 'horas': [5, 2, 3, 0, 1], 'dias': [0, 1, 3, 2, 4]}, '2AMAT': {'profe': 11, 'horas': [4, 4, 5, 0, 0], 'dias': [2, 1, 4, 0, 3]}, '2AING': {'profe': 10, 'horas': [3, 3, 0, 1], 'dias': [1, 0, 4, 2]}, '2AEFI': {'profe': 14, 'horas': [4, 2, 4], 'dias': [3, 0, 4]}, '2ANAT': {'profe': 6, 'horas': [2, 5, 5], 'dias': [2, 3, 1]}, '2ASOC': {'profe': 11, 'horas': [1, 5, 2], 'dias': [0, 2, 4]}, '2ALIB': {'profe': 17, 'horas': [1, 1, 3], 'dias': [3, 1, 2]}, '2AREL': {'profe': 2, 'horas': [3, 2], 'dias': [4, 3]}, '2AART': {'profe': 15, 'horas': [4, 0], 'dias': [0, 1]}, '2BLEN': {'profe': 7, 'horas': [3, 4, 3, 0, 4], 'dias': [3, 0, 4, 2, 1]}, '2BMAT': {'profe': 1, 'horas': [1, 3, 0, 1, 1], 'dias': [2, 1, 0, 3, 4]}, '2BING': {'profe': 11, 'horas': [3, 2, 2, 4], 'dias': [2, 3, 1, 4]}, '2BEFI': {'profe': 14, 'horas': [1, 5, 2], 'dias': [0, 4, 2]}, '2BNAT': {'profe': 15, 'horas': [4, 1, 3], 'dias': [3, 1, 0]}, '2BSOC': {'profe': 4, 'horas': [5, 0, 5], 'dias': [1, 3, 0]}, '2BLIB': {'profe': 17, 'horas': [2, 4, 5], 'dias': [4, 2, 3]}, '2BREL': {'profe': 3, 'horas': [5, 0], 'dias': [2, 4]}, '2BART': {'profe': 4, 'horas': [2, 0], 'dias': [0, 1]}, '3ALEN': {'profe': 6, 'horas': [5, 2, 2, 2, 4], 'dias': [2, 3, 1, 0, 4]}, '3AMAT': {'profe': 2, 'horas': [1, 0, 3, 1, 4], 'dias': [4, 0, 1, 3, 2]}, '3AING': {'profe': 12, 'horas': [0, 0, 1, 0], 'dias': [1, 4, 0, 3]}, '3AEFI': {'profe': 15, 'horas': [1, 4, 2], 'dias': [2, 1, 4]}, '3ANAT': {'profe': 7, 'horas': [5, 4, 3], 'dias': [0, 3, 2]}, '3ASOC': {'profe': 8, 'horas': [5, 0, 4], 'dias': [3, 2, 0]}, '3ALIB': {'profe': 16, 'horas': [5, 5, 3], 'dias': [1, 4, 3]}, '3AREL': {'profe': 2, 'horas': [2, 3], 'dias': [2, 0]}, '3AART': {'profe': 14, 'horas': [3, 1], 'dias': [4, 1]}, '3BLEN': {'profe': 5, 'horas': [5, 1, 2, 2, 3], 'dias': [1, 4, 3, 2, 0]}, '3BMAT': {'profe': 4, 'horas': [4, 1, 5, 4, 4], 'dias': [2, 3, 4, 1, 0]}, '3BING': {'profe': 11, 'horas': [0, 3, 3, 1], 'dias': [4, 3, 1, 2]}, '3BEFI': {'profe': 14, 'horas': [5, 2, 3], 'dias': [0, 1, 2]}, '3BNAT': {'profe': 6, 'horas': [0, 3, 1], 'dias': [3, 4, 0]}, '3BSOC': {'profe': 8, 'horas': [0, 4, 0], 'dias': [0, 4, 1]}, '3BLIB': {'profe': 16, 'horas': [5, 4, 1], 'dias': [2, 3, 1]}, '3BREL': {'profe': 2, 'horas': [5, 2], 'dias': [3, 4]}, '3BART': {'profe': 2, 'horas': [0, 2], 'dias': [2, 0]}, '4ALEN': {'profe': 7, 'horas': [0, 2, 0, 1, 2], 'dias': [3, 2, 4, 1, 0]}, '4AMAT': {'profe': 7, 'horas': [0, 1, 0, 2, 5], 'dias': [1, 2, 0, 4, 3]}, '4AING': {'profe': 12, 'horas': [3, 4, 3, 5], 'dias': [4, 0, 3, 2]}, '4AEFI': {'profe': 14, 'horas': [3, 1, 1], 'dias': [1, 4, 3]}, '4ANAT': {'profe': 3, 'horas': [2, 3, 3], 'dias': [1, 0, 2]}, '4ASOC': {'profe': 13, 'horas': [2, 0, 4], 'dias': [3, 2, 1]}, '4ALIB': {'profe': 16, 'horas': [5, 1, 4], 'dias': [4, 0, 2]}, '4AREL': {'profe': 2, 'horas': [5, 5], 'dias': [1, 0]}, '4AART': {'profe': 9, 'horas': [4, 4], 'dias': [4, 3]}, '4BLEN': {'profe': 9, 'horas': [4, 2, 5, 1, 5], 'dias': [0, 3, 2, 1, 4]}, '4BMAT': {'profe': 5, 'horas': [0, 3, 5, 4, 3], 'dias': [2, 1, 0, 4, 3]}, '4BING': {'profe': 11, 'horas': [1, 5, 2, 5], 'dias': [4, 3, 0, 1]}, '4BEFI': {'profe': 15, 'horas': [2, 2, 0], 'dias': [2, 1, 3]}, '4BNAT': {'profe': 5, 'horas': [0, 2, 3], 'dias': [0, 4, 2]}, '4BSOC': {'profe': 2, 'horas': [4, 0, 1], 'dias': [1, 4, 2]}, '4BLIB': {'profe': 16, 'horas': [1, 4, 4], 'dias': [0, 3, 2]}, '4BREL': {'profe': 3, 'horas': [1, 3], 'dias': [3, 4]}, '4BART': {'profe': 1, 'horas': [3, 0], 'dias': [0, 1]}, '5ALEN': {'profe': 10, 'horas': [4, 5, 2, 5, 5], 'dias': [2, 0, 4, 3, 1]}, '5AMAT': {'profe': 13, 'horas': [2, 1, 4, 3, 5], 'dias': [1, 2, 0, 3, 4]}, '5AING': {'profe': 13, 'horas': [0, 0, 3, 3], 'dias': [4, 3, 1, 2]}, '5AEFI': {'profe': 14, 'horas': [0, 0, 2], 'dias': [0, 2, 3]}, '5ANAT': {'profe': 8, 'horas': [3, 1, 4], 'dias': [0, 4, 1]}, '5ASOC': {'profe': 10, 'horas': [2, 1, 4], 'dias': [0, 3, 4]}, '5ALIB': {'profe': 16, 'horas': [5, 0, 1], 'dias': [2, 1, 0]}, '5AREL': {'profe': 1, 'horas': [1, 4], 'dias': [1, 3]}, '5AART': {'profe': 9, 'horas': [2, 3], 'dias': [2, 4]}, '5BLEN': {'profe': 6, 'horas': [1, 0, 0, 5, 3], 'dias': [2, 1, 0, 4, 3]}, '5BMAT': {'profe': 3, 'horas': [2, 1, 0, 4, 4], 'dias': [4, 0, 3, 2, 1]}, '5BING': {'profe': 13, 'horas': [4, 2, 1, 2], 'dias': [3, 2, 1, 0]}, '5BEFI': {'profe': 14, 'horas': [0, 5, 3], 'dias': [4, 2, 0]}, '5BNAT': {'profe': 7, 'horas': [4, 1, 2], 'dias': [4, 3, 1]}, '5BSOC': {'profe': 13, 'horas': [5, 5, 1], 'dias': [0, 1, 4]}, '5BLIB': {'profe': 17, 'horas': [3, 5, 3], 'dias': [2, 3, 1]}, '5BREL': {'profe': 1, 'horas': [0, 4], 'dias': [2, 0]}, '5BART': {'profe': 1, 'horas': [3, 2], 'dias': [4, 3]}, '6ALEN': {'profe': 8, 'horas': [2, 2, 1, 5, 3], 'dias': [2, 4, 3, 0, 1]}, '6AMAT': {'profe': 5, 'horas': [1, 4, 4, 4, 3], 'dias': [0, 1, 3, 2, 4]}, '6AING': {'profe': 10, 'horas': [5, 3, 2, 0], 'dias': [4, 2, 1, 3]}, '6AEFI': {'profe': 14, 'horas': [4, 5, 1], 'dias': [0, 3, 2]}, '6ANAT': {'profe': 4, 'horas': [0, 0, 1], 'dias': [0, 4, 1]}, '6ASOC': {'profe': 15, 'horas': [1, 5, 3], 'dias': [4, 2, 3]}, '6ALIB': {'profe': 16, 'horas': [0, 2, 0], 'dias': [1, 0, 2]}, '6AREL': {'profe': 1, 'horas': [5, 4], 'dias': [1, 4]}, '6AART': {'profe': 7, 'horas': [3, 2], 'dias': [0, 3]}, '6BLEN': {'profe': 1, 'horas': [5, 4, 0, 3, 3], 'dias': [0, 1, 4, 2, 3]}, '6BMAT': {'profe': 3, 'horas': [2, 1, 2, 1, 1], 'dias': [3, 4, 0, 1, 2]}, '6BING': {'profe': 13, 'horas': [1, 0, 0, 4], 'dias': [3, 1, 0, 2]}, '6BEFI': {'profe': 15, 'horas': [5, 3, 1], 'dias': [4, 1, 0]}, '6BNAT': {'profe': 8, 'horas': [5, 4, 3], 'dias': [2, 3, 4]}, '6BSOC': {'profe': 1, 'horas': [5, 2, 2], 'dias': [3, 1, 4]}, '6BLIB': {'profe': 16, 'horas': [0, 4, 4], 'dias': [2, 0, 4]}, '6BREL': {'profe': 3, 'horas': [2, 5], 'dias': [2, 1]}, '6BART': {'profe': 9, 'horas': [0, 3], 'dias': [3, 0]}}





In [0]:
#Secuencia del proceso
##########################################

#1ªFASE: Asignación de profesores a las asignaturas
#Genera una solucion aleatoria solo con profesores con algoritmo genético que finaliza en 1000 iteraciones
#Se penaliza:
#   1000 por cada hora que un profesor se pasa del maximo de horas a la semana
#   100  por cada profesor que no completa el maximo de horas
#   10   por cada hora que cada profesor no llega al máximo
#   1    por la variabilidad(varianza) de horas asignadas de los  profesores que no llegan al maximo(para que haya uniformidad en la asignación)
#   1    por cada curso que diferente que da cada profesor
#   1    pora las diferencias de los cursos de cada profesor
#POBLACION_INICIAL=main_profesores(PARAMETROS, N_POBLACION, N_PUNTOS_DE_CRUCE, N_MUTACION, N_HIJOS)
#S=POBLACION_INICIAL[0]
#S={"1ALEN": {"profe": 5}, "1AMAT": {"profe": 6}, "1AING": {"profe": 12}, "1AEFI": {"profe": 15}, "1ANAT": {"profe": 8}, "1ASOC": {"profe": 11}, "1ALIB": {"profe": 17}, "1AREL": {"profe": 3}, "1AART": {"profe": 9}, "1BLEN": {"profe": 2}, "1BMAT": {"profe": 9}, "1BING": {"profe": 10}, "1BEFI": {"profe": 15}, "1BNAT": {"profe": 8}, "1BSOC": {"profe": 8}, "1BLIB": {"profe": 16}, "1BREL": {"profe": 3}, "1BART": {"profe": 6}, "2ALEN": {"profe": 9}, "2AMAT": {"profe": 11}, "2AING": {"profe": 10}, "2AEFI": {"profe": 14}, "2ANAT": {"profe": 6}, "2ASOC": {"profe": 11}, "2ALIB": {"profe": 17}, "2AREL": {"profe": 2}, "2AART": {"profe": 15}, "2BLEN": {"profe": 7}, "2BMAT": {"profe": 1}, "2BING": {"profe": 11}, "2BEFI": {"profe": 14}, "2BNAT": {"profe": 15}, "2BSOC": {"profe": 4}, "2BLIB": {"profe": 17}, "2BREL": {"profe": 3}, "2BART": {"profe": 4}, "3ALEN": {"profe": 6}, "3AMAT": {"profe": 2}, "3AING": {"profe": 12}, "3AEFI": {"profe": 15}, "3ANAT": {"profe": 7}, "3ASOC": {"profe": 8}, "3ALIB": {"profe": 16}, "3AREL": {"profe": 2}, "3AART": {"profe": 14}, "3BLEN": {"profe": 5}, "3BMAT": {"profe": 4}, "3BING": {"profe": 11}, "3BEFI": {"profe": 14}, "3BNAT": {"profe": 6}, "3BSOC": {"profe": 15}, "3BLIB": {"profe": 16}, "3BREL": {"profe": 2}, "3BART": {"profe": 2}, "4ALEN": {"profe": 7}, "4AMAT": {"profe": 7}, "4AING": {"profe": 12}, "4AEFI": {"profe": 14}, "4ANAT": {"profe": 3}, "4ASOC": {"profe": 13}, "4ALIB": {"profe": 16}, "4AREL": {"profe": 2}, "4AART": {"profe": 9}, "4BLEN": {"profe": 9}, "4BMAT": {"profe": 5}, "4BING": {"profe": 11}, "4BEFI": {"profe": 15}, "4BNAT": {"profe": 5}, "4BSOC": {"profe": 2}, "4BLIB": {"profe": 16}, "4BREL": {"profe": 3}, "4BART": {"profe": 1}, "5ALEN": {"profe": 10}, "5AMAT": {"profe": 13}, "5AING": {"profe": 13}, "5AEFI": {"profe": 14}, "5ANAT": {"profe": 8}, "5ASOC": {"profe": 10}, "5ALIB": {"profe": 16}, "5AREL": {"profe": 1}, "5AART": {"profe": 9}, "5BLEN": {"profe": 6}, "5BMAT": {"profe": 3}, "5BING": {"profe": 13}, "5BEFI": {"profe": 14}, "5BNAT": {"profe": 7}, "5BSOC": {"profe": 13}, "5BLIB": {"profe": 17}, "5BREL": {"profe": 1}, "5BART": {"profe": 1}, "6ALEN": {"profe": 8}, "6AMAT": {"profe": 5}, "6AING": {"profe": 10}, "6AEFI": {"profe": 14}, "6ANAT": {"profe": 4}, "6ASOC": {"profe": 10}, "6ALIB": {"profe": 16}, "6AREL": {"profe": 1}, "6AART": {"profe": 7}, "6BLEN": {"profe": 1}, "6BMAT": {"profe": 3}, "6BING": {"profe": 13}, "6BEFI": {"profe": 15}, "6BNAT": {"profe": 8}, "6BSOC": {"profe": 1}, "6BLIB": {"profe": 16}, "6BREL": {"profe": 3}, "6BART": {"profe": 9}}
#S={"1ALEN": {"profe": 9}, "1AMAT": {"profe": 14}, "1AING": {"profe": 13}, "1AEFI": {"profe": 14}, "1ANAT": {"profe": 4}, "1ASOC": {"profe": 12}, "1ALIB": {"profe": 16}, "1AREL": {"profe": 2}, "1AART": {"profe": 2}, "1BLEN": {"profe": 3}, "1BMAT": {"profe": 12}, "1BING": {"profe": 13}, "1BEFI": {"profe": 14}, "1BNAT": {"profe": 12}, "1BSOC": {"profe": 2}, "1BLIB": {"profe": 16}, "1BREL": {"profe": 4}, "1BART": {"profe": 2}, "2ALEN": {"profe": 6}, "2AMAT": {"profe": 9}, "2AING": {"profe": 10}, "2AEFI": {"profe": 14}, "2ANAT": {"profe": 5}, "2ASOC": {"profe": 13}, "2ALIB": {"profe": 16}, "2AREL": {"profe": 3}, "2AART": {"profe": 10}, "2BLEN": {"profe": 9}, "2BMAT": {"profe": 2}, "2BING": {"profe": 12}, "2BEFI": {"profe": 14}, "2BNAT": {"profe": 9}, "2BSOC": {"profe": 6}, "2BLIB": {"profe": 16}, "2BREL": {"profe": 3}, "2BART": {"profe": 12}, "3ALEN": {"profe": 2}, "3AMAT": {"profe": 11}, "3AING": {"profe": 13}, "3AEFI": {"profe": 15}, "3ANAT": {"profe": 4}, "3ASOC": {"profe": 8}, "3ALIB": {"profe": 17}, "3AREL": {"profe": 1}, "3AART": {"profe": 6}, "3BLEN": {"profe": 1}, "3BMAT": {"profe": 8}, "3BING": {"profe": 13}, "3BEFI": {"profe": 15}, "3BNAT": {"profe": 8}, "3BSOC": {"profe": 4}, "3BLIB": {"profe": 16}, "3BREL": {"profe": 1}, "3BART": {"profe": 11}, "4ALEN": {"profe": 3}, "4AMAT": {"profe": 11}, "4AING": {"profe": 11}, "4AEFI": {"profe": 14}, "4ANAT": {"profe": 12}, "4ASOC": {"profe": 6}, "4ALIB": {"profe": 16}, "4AREL": {"profe": 2}, "4AART": {"profe": 3}, "4BLEN": {"profe": 4}, "4BMAT": {"profe": 3}, "4BING": {"profe": 13}, "4BEFI": {"profe": 14}, "4BNAT": {"profe": 12}, "4BSOC": {"profe": 6}, "4BLIB": {"profe": 16}, "4BREL": {"profe": 3}, "4BART": {"profe": 2}, "5ALEN": {"profe": 7}, "5AMAT": {"profe": 4}, "5AING": {"profe": 10}, "5AEFI": {"profe": 15}, "5ANAT": {"profe": 7}, "5ASOC": {"profe": 11}, "5ALIB": {"profe": 17}, "5AREL": {"profe": 1}, "5AART": {"profe": 6}, "5BLEN": {"profe": 6}, "5BMAT": {"profe": 9}, "5BING": {"profe": 10}, "5BEFI": {"profe": 15}, "5BNAT": {"profe": 10}, "5BSOC": {"profe": 1}, "5BLIB": {"profe": 16}, "5BREL": {"profe": 4}, "5BART": {"profe": 10}, "6ALEN": {"profe": 7}, "6AMAT": {"profe": 7}, "6AING": {"profe": 11}, "6AEFI": {"profe": 15}, "6ANAT": {"profe": 15}, "6ASOC": {"profe": 8}, "6ALIB": {"profe": 17}, "6AREL": {"profe": 1}, "6AART": {"profe": 7}, "6BLEN": {"profe": 1}, "6BMAT": {"profe": 8}, "6BING": {"profe": 10}, "6BEFI": {"profe": 15}, "6BNAT": {"profe": 7}, "6BSOC": {"profe": 8}, "6BLIB": {"profe": 17}, "6BREL": {"profe": 1}, "6BART": {"profe": 15}}
S={"1ALEN": {"profe": 9}, "1AMAT": {"profe": 11}, "1AING": {"profe": 11}, "1AEFI": {"profe": 14}, "1ANAT": {"profe": 7}, "1ASOC": {"profe": 9}, "1ALIB": {"profe": 16}, "1AREL": {"profe": 1}, "1AART": {"profe": 1}, "1BLEN": {"profe": 7}, "1BMAT": {"profe": 6}, "1BING": {"profe": 11}, "1BEFI": {"profe": 14}, "1BNAT": {"profe": 6}, "1BSOC": {"profe": 9}, "1BLIB": {"profe": 16}, "1BREL": {"profe": 1}, "1BART": {"profe": 6}, "2ALEN": {"profe": 5}, "2AMAT": {"profe": 5}, "2AING": {"profe": 13}, "2AEFI": {"profe": 15}, "2ANAT": {"profe": 13}, "2ASOC": {"profe": 3}, "2ALIB": {"profe": 17}, "2AREL": {"profe": 3}, "2AART": {"profe": 14}, "2BLEN": {"profe": 7}, "2BMAT": {"profe": 6}, "2BING": {"profe": 13}, "2BEFI": {"profe": 14}, "2BNAT": {"profe": 7}, "2BSOC": {"profe": 5}, "2BLIB": {"profe": 17}, "2BREL": {"profe": 3}, "2BART": {"profe": 15}, "3ALEN": {"profe": 1}, "3AMAT": {"profe": 6}, "3AING": {"profe": 10}, "3AEFI": {"profe": 14}, "3ANAT": {"profe": 6}, "3ASOC": {"profe": 14}, "3ALIB": {"profe": 17}, "3AREL": {"profe": 1}, "3AART": {"profe": 1}, "3BLEN": {"profe": 1}, "3BMAT": {"profe": 12}, "3BING": {"profe": 12}, "3BEFI": {"profe": 14}, "3BNAT": {"profe": 14}, "3BSOC": {"profe": 1}, "3BLIB": {"profe": 17}, "3BREL": {"profe": 3}, "3BART": {"profe": 10}, "4ALEN": {"profe": 10}, "4AMAT": {"profe": 3}, "4AING": {"profe": 13}, "4AEFI": {"profe": 15}, "4ANAT": {"profe": 8}, "4ASOC": {"profe": 3}, "4ALIB": {"profe": 17}, "4AREL": {"profe": 3}, "4AART": {"profe": 8}, "4BLEN": {"profe": 13}, "4BMAT": {"profe": 8}, "4BING": {"profe": 10}, "4BEFI": {"profe": 15}, "4BNAT": {"profe": 13}, "4BSOC": {"profe": 8}, "4BLIB": {"profe": 16}, "4BREL": {"profe": 3}, "4BART": {"profe": 3}, "5ALEN": {"profe": 8}, "5AMAT": {"profe": 8}, "5AING": {"profe": 10}, "5AEFI": {"profe": 15}, "5ANAT": {"profe": 7}, "5ASOC": {"profe": 2}, "5ALIB": {"profe": 17}, "5AREL": {"profe": 2}, "5AART": {"profe": 7}, "5BLEN": {"profe": 11}, "5BMAT": {"profe": 11}, "5BING": {"profe": 10}, "5BEFI": {"profe": 15}, "5BNAT": {"profe": 2}, "5BSOC": {"profe": 2}, "5BLIB": {"profe": 16}, "5BREL": {"profe": 4}, "5BART": {"profe": 7}, "6ALEN": {"profe": 2}, "6AMAT": {"profe": 9}, "6AING": {"profe": 12}, "6AEFI": {"profe": 15}, "6ANAT": {"profe": 2}, "6ASOC": {"profe": 5}, "6ALIB": {"profe": 17}, "6AREL": {"profe": 2}, "6AART": {"profe": 9}, "6BLEN": {"profe": 9}, "6BMAT": {"profe": 5}, "6BING": {"profe": 12}, "6BEFI": {"profe": 15}, "6BNAT": {"profe": 12}, "6BSOC": {"profe": 12}, "6BLIB": {"profe": 16}, "6BREL": {"profe": 2}, "6BART": {"profe": 5}} 

asignaturas_impartidas_x_profesor(S)
print(S)
print('********FIN DE LA FASE 1\n') 

#2ªFASE: Obtencion de solución con horarios.
#Genera una solucion básica con horarios.Todos los cursos tienen las asignaturas asignadas correctamente pero 
#   hay profesores que repiten horas
S2=genera_solucion_horarios(S, PARAMETROS)
#S2={'1ALEN': {'profe': 10, 'horas': [1, 5, 0, 4, 2], 'dias': [2, 0, 3, 4, 1]}, '1AMAT': {'profe': 1, 'horas': [0, 1, 0, 4, 1], 'dias': [2, 3, 1, 0, 4]}, '1AING': {'profe': 11, 'horas': [3, 4, 3, 0], 'dias': [0, 2, 1, 4]}, '1AEFI': {'profe': 15, 'horas': [3, 5, 5], 'dias': [3, 1, 4]}, '1ANAT': {'profe': 12, 'horas': [4, 3, 1], 'dias': [3, 2, 0]}, '1ASOC': {'profe': 6, 'horas': [1, 2, 2], 'dias': [1, 0, 4]}, '1ALIB': {'profe': 17, 'horas': [5, 2, 4], 'dias': [2, 3, 1]}, '1AREL': {'profe': 1, 'horas': [0, 5], 'dias': [0, 3]}, '1AART': {'profe': 12, 'horas': [3, 2], 'dias': [4, 2]}, '1BLEN': {'profe': 10, 'horas': [3, 5, 4, 0, 5], 'dias': [1, 2, 0, 3, 4]}, '1BMAT': {'profe': 7, 'horas': [0, 1, 4, 1, 1], 'dias': [1, 0, 3, 2, 4]}, '1BING': {'profe': 11, 'horas': [1, 2, 2, 0], 'dias': [1, 0, 4, 2]}, '1BEFI': {'profe': 15, 'horas': [3, 3, 0], 'dias': [3, 2, 0]}, '1BNAT': {'profe': 14, 'horas': [1, 2, 3], 'dias': [3, 1, 4]}, '1BSOC': {'profe': 13, 'horas': [2, 3, 4], 'dias': [2, 0, 4]}, '1BLIB': {'profe': 16, 'horas': [4, 5, 0], 'dias': [1, 3, 4]}, '1BREL': {'profe': 4, 'horas': [5, 4], 'dias': [1, 2]}, '1BART': {'profe': 9, 'horas': [5, 2], 'dias': [0, 3]}, '2ALEN': {'profe': 2, 'horas': [0, 3, 3, 3, 0], 'dias': [2, 0, 3, 4, 1]}, '2AMAT': {'profe': 3, 'horas': [4, 2, 4, 1, 0], 'dias': [0, 2, 1, 3, 4]}, '2AING': {'profe': 11, 'horas': [5, 3, 1, 4], 'dias': [2, 1, 0, 4]}, '2AEFI': {'profe': 14, 'horas': [2, 1, 5], 'dias': [3, 2, 0]}, '2ANAT': {'profe': 8, 'horas': [5, 1, 5], 'dias': [3, 4, 1]}, '2ASOC': {'profe': 6, 'horas': [2, 3, 4], 'dias': [1, 2, 3]}, '2ALIB': {'profe': 16, 'horas': [2, 5, 0], 'dias': [0, 4, 3]}, '2AREL': {'profe': 1, 'horas': [1, 2], 'dias': [1, 4]}, '2AART': {'profe': 10, 'horas': [0, 4], 'dias': [0, 2]}, '2BLEN': {'profe': 10, 'horas': [2, 4, 2, 0, 2], 'dias': [3, 1, 4, 2, 0]}, '2BMAT': {'profe': 4, 'horas': [4, 1, 2, 4, 3], 'dias': [4, 0, 2, 3, 1]}, '2BING': {'profe': 13, 'horas': [1, 0, 5, 5], 'dias': [1, 4, 2, 0]}, '2BEFI': {'profe': 15, 'horas': [3, 3, 0], 'dias': [3, 2, 0]}, '2BNAT': {'profe': 7, 'horas': [2, 0, 1], 'dias': [1, 3, 4]}, '2BSOC': {'profe': 5, 'horas': [5, 5, 4], 'dias': [1, 3, 0]}, '2BLIB': {'profe': 17, 'horas': [4, 3, 1], 'dias': [2, 4, 3]}, '2BREL': {'profe': 4, 'horas': [5, 3], 'dias': [4, 0]}, '2BART': {'profe': 3, 'horas': [1, 0], 'dias': [2, 1]}, '3ALEN': {'profe': 3, 'horas': [5, 2, 1, 2, 2], 'dias': [0, 3, 4, 2, 1]}, '3AMAT': {'profe': 2, 'horas': [3, 3, 5, 0, 3], 'dias': [1, 0, 2, 4, 3]}, '3AING': {'profe': 13, 'horas': [4, 2, 4, 1], 'dias': [1, 4, 0, 3]}, '3AEFI': {'profe': 14, 'horas': [1, 3, 1], 'dias': [2, 4, 0]}, '3ANAT': {'profe': 5, 'horas': [1, 3, 0], 'dias': [1, 2, 3]}, '3ASOC': {'profe': 5, 'horas': [0, 5, 4], 'dias': [0, 3, 2]}, '3ALIB': {'profe': 16, 'horas': [5, 5, 2], 'dias': [1, 4, 0]}, '3AREL': {'profe': 2, 'horas': [4, 0], 'dias': [3, 1]}, '3AART': {'profe': 12, 'horas': [0, 4], 'dias': [2, 4]}, '3BLEN': {'profe': 7, 'horas': [3, 0, 0, 2, 1], 'dias': [2, 3, 0, 4, 1]}, '3BMAT': {'profe': 2, 'horas': [4, 1, 2, 1, 0], 'dias': [3, 0, 2, 4, 1]}, '3BING': {'profe': 11, 'horas': [0, 2, 1, 3], 'dias': [4, 1, 3, 0]}, '3BEFI': {'profe': 14, 'horas': [4, 3, 3], 'dias': [2, 4, 3]}, '3BNAT': {'profe': 5, 'horas': [5, 1, 5], 'dias': [0, 2, 1]}, '3BSOC': {'profe': 1, 'horas': [4, 0, 2], 'dias': [4, 2, 0]}, '3BLIB': {'profe': 17, 'horas': [3, 2, 5], 'dias': [1, 3, 2]}, '3BREL': {'profe': 1, 'horas': [4, 4], 'dias': [1, 0]}, '3BART': {'profe': 6, 'horas': [5, 5], 'dias': [3, 4]}, '4ALEN': {'profe': 8, 'horas': [3, 4, 5, 1, 3], 'dias': [2, 1, 0, 3, 4]}, '4AMAT': {'profe': 9, 'horas': [4, 4, 0, 2, 5], 'dias': [0, 4, 1, 2, 3]}, '4AING': {'profe': 12, 'horas': [5, 1, 0, 2], 'dias': [2, 4, 0, 1]}, '4AEFI': {'profe': 15, 'horas': [3, 2, 1], 'dias': [3, 0, 1]}, '4ANAT': {'profe': 9, 'horas': [1, 5, 4], 'dias': [2, 4, 3]}, '4ASOC': {'profe': 5, 'horas': [3, 3, 4], 'dias': [0, 1, 2]}, '4ALIB': {'profe': 16, 'horas': [2, 0, 1], 'dias': [3, 4, 0]}, '4AREL': {'profe': 2, 'horas': [5, 0], 'dias': [1, 2]}, '4AART': {'profe': 4, 'horas': [0, 2], 'dias': [3, 4]}, '4BLEN': {'profe': 7, 'horas': [5, 0, 0, 5, 4], 'dias': [0, 1, 4, 3, 2]}, '4BMAT': {'profe': 8, 'horas': [3, 4, 3, 3, 5], 'dias': [0, 4, 2, 3, 1]}, '4BING': {'profe': 11, 'horas': [1, 1, 3, 2], 'dias': [4, 0, 1, 3]}, '4BEFI': {'profe': 14, 'horas': [0, 5, 0], 'dias': [2, 4, 0]}, '4BNAT': {'profe': 10, 'horas': [5, 4, 4], 'dias': [2, 1, 3]}, '4BSOC': {'profe': 9, 'horas': [1, 2, 2], 'dias': [3, 2, 1]}, '4BLIB': {'profe': 16, 'horas': [3, 4, 1], 'dias': [4, 0, 1]}, '4BREL': {'profe': 4, 'horas': [2, 1], 'dias': [4, 2]}, '4BART': {'profe': 9, 'horas': [0, 2], 'dias': [3, 0]}, '5ALEN': {'profe': 6, 'horas': [2, 5, 1, 1, 5], 'dias': [0, 2, 1, 3, 4]}, '5AMAT': {'profe': 8, 'horas': [2, 0, 1, 5, 3], 'dias': [2, 1, 4, 3, 0]}, '5AING': {'profe': 12, 'horas': [3, 3, 4, 0], 'dias': [3, 4, 1, 2]}, '5AEFI': {'profe': 14, 'horas': [5, 3, 0], 'dias': [0, 2, 3]}, '5ANAT': {'profe': 4, 'horas': [3, 2, 4], 'dias': [1, 4, 0]}, '5ASOC': {'profe': 10, 'horas': [4, 4, 2], 'dias': [4, 2, 1]}, '5ALIB': {'profe': 17, 'horas': [2, 0, 0], 'dias': [3, 0, 4]}, '5AREL': {'profe': 1, 'horas': [1, 4], 'dias': [2, 3]}, '5AART': {'profe': 8, 'horas': [1, 5], 'dias': [0, 1]}, '5BLEN': {'profe': 5, 'horas': [4, 3, 1, 1, 1], 'dias': [2, 3, 1, 4, 0]}, '5BMAT': {'profe': 1, 'horas': [0, 3, 4, 3, 2], 'dias': [3, 0, 1, 4, 2]}, '5BING': {'profe': 13, 'horas': [2, 5, 5, 5], 'dias': [3, 1, 4, 0]}, '5BEFI': {'profe': 15, 'horas': [3, 4, 5], 'dias': [2, 4, 3]}, '5BNAT': {'profe': 5, 'horas': [5, 4, 3], 'dias': [2, 0, 1]}, '5BSOC': {'profe': 9, 'horas': [1, 1, 0], 'dias': [3, 2, 0]}, '5BLIB': {'profe': 17, 'horas': [2, 2, 0], 'dias': [4, 1, 2]}, '5BREL': {'profe': 2, 'horas': [2, 4], 'dias': [0, 3]}, '5BART': {'profe': 15, 'horas': [0, 0], 'dias': [1, 4]}, '6ALEN': {'profe': 12, 'horas': [0, 2, 0, 4, 3], 'dias': [2, 3, 0, 1, 4]}, '6AMAT': {'profe': 4, 'horas': [3, 0, 5, 5, 5], 'dias': [2, 4, 1, 3, 0]}, '6AING': {'profe': 13, 'horas': [2, 1, 3, 1], 'dias': [4, 1, 3, 2]}, '6AEFI': {'profe': 15, 'horas': [4, 0, 1], 'dias': [0, 1, 4]}, '6ANAT': {'profe': 8, 'horas': [1, 5, 0], 'dias': [0, 2, 3]}, '6ASOC': {'profe': 11, 'horas': [2, 4, 2], 'dias': [0, 2, 1]}, '6ALIB': {'profe': 17, 'horas': [4, 4, 2], 'dias': [3, 4, 2]}, '6AREL': {'profe': 2, 'horas': [1, 5], 'dias': [3, 4]}, '6AART': {'profe': 4, 'horas': [3, 3], 'dias': [0, 1]}, '6BLEN': {'profe': 9, 'horas': [0, 0, 3, 3, 1], 'dias': [4, 3, 2, 1, 0]}, '6BMAT': {'profe': 7, 'horas': [1, 3, 2, 3, 3], 'dias': [1, 0, 2, 3, 4]}, '6BING': {'profe': 13, 'horas': [0, 2, 4, 1], 'dias': [0, 1, 2, 4]}, '6BEFI': {'profe': 15, 'horas': [2, 4, 0], 'dias': [3, 4, 1]}, '6BNAT': {'profe': 14, 'horas': [0, 4, 5], 'dias': [2, 3, 0]}, '6BSOC': {'profe': 12, 'horas': [1, 5, 4], 'dias': [2, 3, 0]}, '6BLIB': {'profe': 16, 'horas': [2, 5, 1], 'dias': [4, 1, 3]}, '6BREL': {'profe': 1, 'horas': [5, 2], 'dias': [2, 0]}, '6BART': {'profe': 14, 'horas': [4, 5], 'dias': [1, 4]}}

print(S2)
print('********FIN DE LA FASE 2\n') 


#3ª Refinamiento de la solución de la fase 2ª por busqueda por algoritmo evolutivo de mejores soluciones(profesores sin horas repetidas)
#La funcion evalua_solucion_horarios es la que determinará la búsqueda por el algoritmo evolutivo
#    W1 = 1000  #Peso para penalizar por cada hora en que un profesor repite dia y hora
#         1000    por cada hora que un profesor se pasa del maximo
#    W2  =100   #Peso por cada profesor que no completa el maximo de horas
#    W3 = 10    #Peso por cada hora libre que no es la ultima o la primera del dia
#    W4 = 1     #Peso por la variabilidad de las horas libres que no sean al principio y al final del dias
 
S3=main_evolutivo(SOLUCION=S2 , PARAMETROS=PARAMETROS, N_POBLACION=N_POBLACION , modo="max_horas" ) 
#S3={'1ALEN': {'profe': 8, 'horas': [1, 4, 4, 3, 1], 'dias': [1, 2, 3, 0, 4]}, '1AMAT': {'profe': 3, 'horas': [5, 0, 1, 5, 4], 'dias': [4, 1, 2, 3, 0]}, '1AING': {'profe': 12, 'horas': [0, 2, 3, 2], 'dias': [2, 3, 1, 4]}, '1AEFI': {'profe': 14, 'horas': [1, 1, 3], 'dias': [0, 3, 2]}, '1ANAT': {'profe': 2, 'horas': [5, 4, 2], 'dias': [0, 4, 1]}, '1ASOC': {'profe': 6, 'horas': [2, 3, 5], 'dias': [0, 3, 1]}, '1ALIB': {'profe': 17, 'horas': [0, 5, 0], 'dias': [4, 2, 0]}, '1AREL': {'profe': 2, 'horas': [0, 2], 'dias': [3, 2]}, '1AART': {'profe': 4, 'horas': [3, 4], 'dias': [4, 1]}, '1BLEN': {'profe': 5, 'horas': [0, 0, 4, 3, 2], 'dias': [0, 3, 1, 2, 4]}, '1BMAT': {'profe': 10, 'horas': [3, 4, 5, 3, 0], 'dias': [0, 3, 2, 1, 4]}, '1BING': {'profe': 13, 'horas': [1, 5, 1, 4], 'dias': [1, 4, 2, 0]}, '1BEFI': {'profe': 15, 'horas': [1, 2, 3], 'dias': [3, 1, 4]}, '1BNAT': {'profe': 5, 'horas': [2, 2, 2], 'dias': [0, 3, 2]}, '1BSOC': {'profe': 4, 'horas': [4, 0, 5], 'dias': [4, 1, 0]}, '1BLIB': {'profe': 16, 'horas': [3, 4, 1], 'dias': [3, 2, 0]}, '1BREL': {'profe': 2, 'horas': [1, 5], 'dias': [4, 1]}, '1BART': {'profe': 2, 'horas': [0, 5], 'dias': [2, 3]}, '2ALEN': {'profe': 4, 'horas': [3, 4, 4, 1, 2], 'dias': [0, 3, 2, 1, 4]}, '2AMAT': {'profe': 1, 'horas': [0, 5, 0, 3, 3], 'dias': [4, 1, 0, 3, 2]}, '2AING': {'profe': 11, 'horas': [0, 5, 3, 1], 'dias': [3, 4, 1, 0]}, '2AEFI': {'profe': 14, 'horas': [2, 4, 4], 'dias': [2, 1, 0]}, '2ANAT': {'profe': 3, 'horas': [3, 0, 2], 'dias': [4, 2, 3]}, '2ASOC': {'profe': 5, 'horas': [4, 0, 1], 'dias': [4, 1, 2]}, '2ALIB': {'profe': 16, 'horas': [2, 1, 1], 'dias': [0, 3, 4]}, '2AREL': {'profe': 4, 'horas': [2, 5], 'dias': [1, 2]}, '2AART': {'profe': 5, 'horas': [5, 5], 'dias': [0, 3]}, '2BLEN': {'profe': 6, 'horas': [5, 0, 1, 0, 4], 'dias': [2, 1, 0, 3, 4]}, '2BMAT': {'profe': 3, 'horas': [5, 3, 2, 0, 2], 'dias': [1, 3, 4, 0, 2]}, '2BING': {'profe': 12, 'horas': [4, 1, 5, 4], 'dias': [1, 3, 4, 0]}, '2BEFI': {'profe': 14, 'horas': [0, 0, 2], 'dias': [2, 4, 0]}, '2BNAT': {'profe': 1, 'horas': [1, 3, 5], 'dias': [2, 1, 3]}, '2BSOC': {'profe': 5, 'horas': [3, 2, 3], 'dias': [4, 1, 0]}, '2BLIB': {'profe': 17, 'horas': [3, 2, 1], 'dias': [2, 3, 1]}, '2BREL': {'profe': 3, 'horas': [1, 5], 'dias': [4, 0]}, '2BART': {'profe': 5, 'horas': [4, 4], 'dias': [2, 3]}, '3ALEN': {'profe': 6, 'horas': [4, 4, 3, 3, 2], 'dias': [3, 0, 4, 1, 2]}, '3AMAT': {'profe': 11, 'horas': [4, 1, 3, 2, 5], 'dias': [4, 2, 0, 3, 1]}, '3AING': {'profe': 12, 'horas': [5, 2, 2, 5], 'dias': [3, 1, 0, 2]}, '3AEFI': {'profe': 15, 'horas': [1, 4, 0], 'dias': [4, 2, 0]}, '3ANAT': {'profe': 2, 'horas': [3, 4, 5], 'dias': [3, 1, 4]}, '3ASOC': {'profe': 12, 'horas': [5, 3, 1], 'dias': [0, 2, 1]}, '3ALIB': {'profe': 17, 'horas': [0, 2, 0], 'dias': [3, 4, 2]}, '3AREL': {'profe': 2, 'horas': [1, 0], 'dias': [3, 4]}, '3AART': {'profe': 12, 'horas': [0, 1], 'dias': [1, 0]}, '3BLEN': {'profe': 5, 'horas': [4, 5, 3, 5, 3], 'dias': [0, 2, 3, 4, 1]}, '3BMAT': {'profe': 1, 'horas': [5, 4, 2, 2, 4], 'dias': [0, 4, 3, 1, 2]}, '3BING': {'profe': 10, 'horas': [3, 1, 0, 0], 'dias': [4, 0, 3, 2]}, '3BEFI': {'profe': 14, 'horas': [0, 5, 2], 'dias': [1, 3, 4]}, '3BNAT': {'profe': 3, 'horas': [3, 4, 2], 'dias': [2, 1, 0]}, '3BSOC': {'profe': 15, 'horas': [1, 3, 1], 'dias': [1, 0, 2]}, '3BLIB': {'profe': 16, 'horas': [0, 4, 0], 'dias': [4, 3, 0]}, '3BREL': {'profe': 4, 'horas': [1, 5], 'dias': [4, 1]}, '3BART': {'profe': 11, 'horas': [2, 1], 'dias': [2, 3]}, '4ALEN': {'profe': 7, 'horas': [1, 2, 1, 1, 4], 'dias': [4, 2, 0, 1, 3]}, '4AMAT': {'profe': 8, 'horas': [5, 3, 5, 2, 3], 'dias': [0, 2, 1, 3, 4]}, '4AING': {'profe': 13, 'horas': [2, 4, 3, 4], 'dias': [0, 4, 3, 2]}, '4AEFI': {'profe': 15, 'horas': [4, 5, 5], 'dias': [1, 3, 4]}, '4ANAT': {'profe': 9, 'horas': [3, 0, 4], 'dias': [1, 2, 0]}, '4ASOC': {'profe': 4, 'horas': [0, 0, 0], 'dias': [1, 4, 0]}, '4ALIB': {'profe': 16, 'horas': [5, 1, 2], 'dias': [2, 3, 4]}, '4AREL': {'profe': 2, 'horas': [3, 1], 'dias': [0, 2]}, '4AART': {'profe': 13, 'horas': [2, 0], 'dias': [1, 3]}, '4BLEN': {'profe': 7, 'horas': [2, 1, 1, 2, 2], 'dias': [1, 3, 2, 4, 0]}, '4BMAT': {'profe': 9, 'horas': [0, 5, 0, 4, 5], 'dias': [0, 1, 3, 2, 4]}, '4BING': {'profe': 11, 'horas': [3, 4, 5, 3], 'dias': [4, 1, 2, 3]}, '4BEFI': {'profe': 15, 'horas': [1, 0, 0], 'dias': [0, 1, 2]}, '4BNAT': {'profe': 11, 'horas': [4, 0, 5], 'dias': [3, 4, 0]}, '4BSOC': {'profe': 7, 'horas': [4, 5, 3], 'dias': [4, 3, 2]}, '4BLIB': {'profe': 17, 'horas': [1, 3, 2], 'dias': [1, 0, 2]}, '4BREL': {'profe': 4, 'horas': [3, 4], 'dias': [1, 0]}, '4BART': {'profe': 10, 'horas': [1, 2], 'dias': [4, 3]}, '5ALEN': {'profe': 11, 'horas': [1, 5, 3, 2, 1], 'dias': [4, 3, 2, 0, 1]}, '5AMAT': {'profe': 13, 'horas': [5, 0, 4, 3, 0], 'dias': [0, 2, 3, 4, 1]}, '5AING': {'profe': 10, 'horas': [5, 0, 4, 1], 'dias': [1, 0, 4, 2]}, '5AEFI': {'profe': 15, 'horas': [0, 4, 5], 'dias': [3, 0, 2]}, '5ANAT': {'profe': 10, 'horas': [2, 1, 2], 'dias': [1, 3, 4]}, '5ASOC': {'profe': 6, 'horas': [4, 3, 4], 'dias': [1, 0, 2]}, '5ALIB': {'profe': 17, 'horas': [5, 3, 1], 'dias': [4, 3, 0]}, '5AREL': {'profe': 4, 'horas': [2, 2], 'dias': [2, 3]}, '5AART': {'profe': 7, 'horas': [3, 0], 'dias': [1, 4]}, '5BLEN': {'profe': 7, 'horas': [3, 0, 4, 4, 4], 'dias': [4, 3, 2, 0, 1]}, '5BMAT': {'profe': 10, 'horas': [5, 3, 0, 5, 5], 'dias': [4, 2, 1, 0, 3]}, '5BING': {'profe': 12, 'horas': [2, 3, 1, 0], 'dias': [2, 3, 4, 0]}, '5BEFI': {'profe': 14, 'horas': [5, 2, 5], 'dias': [1, 3, 2]}, '5BNAT': {'profe': 2, 'horas': [2, 2, 3], 'dias': [0, 4, 1]}, '5BSOC': {'profe': 9, 'horas': [4, 1, 0], 'dias': [3, 0, 4]}, '5BLIB': {'profe': 16, 'horas': [0, 1, 4], 'dias': [2, 1, 4]}, '5BREL': {'profe': 3, 'horas': [1, 2], 'dias': [3, 1]}, '5BART': {'profe': 12, 'horas': [1, 3], 'dias': [2, 0]}, '6ALEN': {'profe': 14, 'horas': [5, 2, 1, 1, 0], 'dias': [0, 1, 4, 2, 3]}, '6AMAT': {'profe': 8, 'horas': [1, 0, 3, 5, 5], 'dias': [0, 1, 3, 4, 2]}, '6AING': {'profe': 13, 'horas': [3, 4, 2, 3], 'dias': [0, 1, 4, 2]}, '6AEFI': {'profe': 15, 'horas': [2, 5, 2], 'dias': [3, 1, 2]}, '6ANAT': {'profe': 8, 'horas': [4, 1, 2], 'dias': [4, 3, 0]}, '6ASOC': {'profe': 3, 'horas': [0, 3, 4], 'dias': [4, 1, 3]}, '6ALIB': {'profe': 17, 'horas': [0, 0, 5], 'dias': [0, 2, 3]}, '6AREL': {'profe': 2, 'horas': [4, 1], 'dias': [0, 1]}, '6AART': {'profe': 2, 'horas': [3, 4], 'dias': [4, 2]}, '6BLEN': {'profe': 8, 'horas': [4, 2, 0, 0, 2], 'dias': [0, 1, 3, 2, 4]}, '6BMAT': {'profe': 9, 'horas': [2, 1, 5, 4, 4], 'dias': [3, 2, 0, 1, 4]}, '6BING': {'profe': 13, 'horas': [5, 5, 5, 1], 'dias': [2, 3, 1, 4]}, '6BEFI': {'profe': 14, 'horas': [0, 4, 3], 'dias': [0, 2, 4]}, '6BNAT': {'profe': 7, 'horas': [3, 0, 3], 'dias': [0, 1, 3]}, '6BSOC': {'profe': 1, 'horas': [1, 2, 1], 'dias': [1, 2, 3]}, '6BLIB': {'profe': 16, 'horas': [1, 0, 4], 'dias': [0, 4, 3]}, '6BREL': {'profe': 4, 'horas': [2, 5], 'dias': [0, 4]}, '6BART': {'profe': 15, 'horas': [3, 3], 'dias': [1, 2]}}

print(S3)
print('********FIN DE LA FASE 3\n') 

S4=main_evolutivo(SOLUCION=S3 , PARAMETROS=PARAMETROS, N_POBLACION=N_POBLACION , modo="no_max_horas" ) 
print(S4)

print("****La mejor solución encontrada es:", json.dumps(S4))


#PENDIENTE. Mejoras
#Evitar que haya dias con solo una hora lectiva
#Tratar de acumular o dispersar las horas libres de los profesores
#Informe general de la bondad de la solucion e imprimir horarios por curso y por profesor.



Profe: 1  total horas: 23  asignaturas: ['1AREL', '1AART', '1BREL', '3ALEN', '3AREL', '3AART', '3BLEN', '3BSOC']
Profe: 2  total horas: 23  asignaturas: ['5ASOC', '5AREL', '5BNAT', '5BSOC', '6ALEN', '6ANAT', '6AREL', '6BREL']
Profe: 3  total horas: 23  asignaturas: ['2ASOC', '2AREL', '2BREL', '3BREL', '4AMAT', '4ASOC', '4AREL', '4BREL', '4BART']
Profe: 4  total horas: 5BREL  asignaturas: ['5BREL']
Profe: 5  total horas: 23  asignaturas: ['2ALEN', '2AMAT', '2BSOC', '6ASOC', '6BMAT', '6BART']
Profe: 6  total horas: 23  asignaturas: ['1BMAT', '1BNAT', '1BART', '2BMAT', '3AMAT', '3ANAT']
Profe: 7  total horas: 23  asignaturas: ['1ANAT', '1BLEN', '2BLEN', '2BNAT', '5ANAT', '5AART', '5BART']
Profe: 8  total horas: 23  asignaturas: ['4ANAT', '4AART', '4BMAT', '4BSOC', '5ALEN', '5AMAT']
Profe: 9  total horas: 23  asignaturas: ['1ALEN', '1ASOC', '1BSOC', '6AMAT', '6AART', '6BLEN']
Profe: 10  total horas: 23  asignaturas: ['3AING', '3BART', '4ALEN', '4BING', '5AING', '5BING']
Profe: 11  total ho

In [0]:
PP={"1ALEN": {"profe": 9, "horas": [4, 2, 4, 5, 4], "dias": [2, 2, 0, 0, 1]}, "1AMAT": {"profe": 5, "horas": [1, 2, 1, 5, 3], "dias": [0, 3, 1, 2, 3]}, "1AING": {"profe": 12, "horas": [5, 5, 0, 0], "dias": [0, 1, 4, 2]}, "1AEFI": {"profe": 15, "horas": [5, 1, 4], "dias": [1, 2, 3]}, "1ANAT": {"profe": 2, "horas": [0, 1, 2], "dias": [3, 2, 4]}, "1ASOC": {"profe": 7, "horas": [0, 0, 5], "dias": [3, 0, 4]}, "1ALIB": {"profe": 16, "horas": [2, 2, 2], "dias": [2, 1, 0]}, "1AREL": {"profe": 2, "horas": [0, 3], "dias": [1, 0]}, "1AART": {"profe": 9, "horas": [5, 5], "dias": [3, 2]}, "1BLEN": {"profe": 4, "horas": [1, 3, 1, 3, 0], "dias": [2, 0, 3, 1, 3]}, "1BMAT": {"profe": 1, "horas": [0, 2, 2, 4, 1], "dias": [4, 2, 0, 1, 4]}, "1BING": {"profe": 13, "horas": [4, 5, 3, 2], "dias": [3, 2, 4, 0]}, "1BEFI": {"profe": 14, "horas": [3, 5, 5], "dias": [2, 1, 2]}, "1BNAT": {"profe": 3, "horas": [4, 0, 4], "dias": [3, 4, 4]}, "1BSOC": {"profe": 11, "horas": [3, 4, 1], "dias": [2, 1, 1]}, "1BLIB": {"profe": 16, "horas": [5, 3, 4], "dias": [0, 1, 2]}, "1BREL": {"profe": 2, "horas": [0, 0], "dias": [0, 4]}, "1BART": {"profe": 13, "horas": [0, 3], "dias": [1, 3]}, "2ALEN": {"profe": 9, "horas": [2, 3, 3, 1, 4], "dias": [4, 4, 1, 1, 4]}, "2AMAT": {"profe": 2, "horas": [1, 2, 5, 4, 1], "dias": [3, 3, 4, 3, 4]}, "2AING": {"profe": 13, "horas": [1, 4, 3, 0], "dias": [2, 4, 0, 4]}, "2AEFI": {"profe": 15, "horas": [2, 3, 0], "dias": [3, 4, 3]}, "2ANAT": {"profe": 8, "horas": [1, 2, 3], "dias": [3, 2, 3]}, "2ASOC": {"profe": 10, "horas": [0, 0, 3], "dias": [2, 4, 0]}, "2ALIB": {"profe": 17, "horas": [2, 2, 5], "dias": [1, 0, 4]}, "2AREL": {"profe": 1, "horas": [5, 3], "dias": [3, 4]}, "2AART": {"profe": 12, "horas": [2, 4], "dias": [0, 4]}, "2BLEN": {"profe": 8, "horas": [2, 2, 3, 2, 4], "dias": [1, 4, 4, 0, 3]}, "2BMAT": {"profe": 10, "horas": [5, 1, 5, 1, 2], "dias": [3, 4, 0, 3, 3]}, "2BING": {"profe": 13, "horas": [4, 4, 1, 5], "dias": [2, 0, 0, 3]}, "2BEFI": {"profe": 15, "horas": [5, 5, 4], "dias": [3, 2, 4]}, "2BNAT": {"profe": 9, "horas": [0, 3, 1], "dias": [3, 0, 0]}, "2BSOC": {"profe": 11, "horas": [3, 1, 0], "dias": [3, 0, 0]}, "2BLIB": {"profe": 17, "horas": [3, 2, 1], "dias": [2, 1, 3]}, "2BREL": {"profe": 4, "horas": [0, 2], "dias": [0, 2]}, "2BART": {"profe": 6, "horas": [1, 0], "dias": [0, 1]}, "3ALEN": {"profe": 3, "horas": [0, 4, 4, 1, 3], "dias": [1, 0, 1, 0, 0]}, "3AMAT": {"profe": 7, "horas": [2, 1, 3, 2, 4], "dias": [0, 0, 3, 4, 0]}, "3AING": {"profe": 12, "horas": [5, 3, 4, 0], "dias": [2, 4, 0, 3]}, "3AEFI": {"profe": 15, "horas": [2, 0, 1], "dias": [4, 1, 4]}, "3ANAT": {"profe": 6, "horas": [0, 5, 5], "dias": [3, 0, 3]}, "3ASOC": {"profe": 10, "horas": [2, 4, 2], "dias": [2, 1, 1]}, "3ALIB": {"profe": 17, "horas": [3, 1, 0], "dias": [4, 1, 0]}, "3AREL": {"profe": 3, "horas": [0, 5], "dias": [0, 3]}, "3AART": {"profe": 15, "horas": [1, 3], "dias": [1, 1]}, "3BLEN": {"profe": 1, "horas": [4, 4, 1, 5, 2], "dias": [3, 0, 2, 1, 3]}, "3BMAT": {"profe": 14, "horas": [0, 4, 1, 2, 1], "dias": [4, 1, 1, 2, 2]}, "3BING": {"profe": 13, "horas": [1, 0, 5, 5], "dias": [1, 0, 0, 1]}, "3BEFI": {"profe": 14, "horas": [5, 0, 2], "dias": [4, 3, 3]}, "3BNAT": {"profe": 3, "horas": [2, 5, 0], "dias": [4, 0, 3]}, "3BSOC": {"profe": 7, "horas": [0, 3, 1], "dias": [1, 4, 3]}, "3BLIB": {"profe": 16, "horas": [3, 0, 3], "dias": [3, 2, 1]}, "3BREL": {"profe": 1, "horas": [0, 1], "dias": [0, 3]}, "3BART": {"profe": 8, "horas": [1, 0], "dias": [0, 2]}, "4ALEN": {"profe": 13, "horas": [3, 1, 2, 1, 2], "dias": [2, 3, 1, 4, 2]}, "4AMAT": {"profe": 6, "horas": [5, 1, 1, 2, 3], "dias": [4, 4, 2, 3, 1]}, "4AING": {"profe": 11, "horas": [2, 0, 5, 2], "dias": [1, 3, 1, 0]}, "4AEFI": {"profe": 14, "horas": [1, 2, 0], "dias": [0, 4, 1]}, "4ANAT": {"profe": 8, "horas": [0, 5, 5], "dias": [0, 0, 4]}, "4ASOC": {"profe": 6, "horas": [5, 0, 3], "dias": [2, 0, 2]}, "4ALIB": {"profe": 17, "horas": [1, 5, 3], "dias": [1, 4, 0]}, "4AREL": {"profe": 4, "horas": [4, 4], "dias": [4, 2]}, "4AART": {"profe": 6, "horas": [4, 4], "dias": [1, 2]}, "4BLEN": {"profe": 7, "horas": [2, 2, 2, 5, 4], "dias": [1, 3, 2, 0, 2]}, "4BMAT": {"profe": 1, "horas": [3, 1, 5, 3, 4], "dias": [0, 0, 2, 3, 4]}, "4BING": {"profe": 10, "horas": [3, 1, 5, 2], "dias": [1, 2, 4, 4]}, "4BEFI": {"profe": 15, "horas": [1, 5, 3], "dias": [3, 0, 2]}, "4BNAT": {"profe": 15, "horas": [1, 4, 5], "dias": [0, 1, 4]}, "4BSOC": {"profe": 8, "horas": [3, 4, 0], "dias": [1, 0, 3]}, "4BLIB": {"profe": 16, "horas": [1, 0, 4], "dias": [1, 2, 3]}, "4BREL": {"profe": 1, "horas": [4, 3], "dias": [2, 1]}, "4BART": {"profe": 8, "horas": [1, 5], "dias": [1, 2]}, "5ALEN": {"profe": 5, "horas": [0, 2, 5, 2, 4], "dias": [4, 2, 0, 4, 2]}, "5AMAT": {"profe": 6, "horas": [0, 4, 1, 2, 4], "dias": [2, 4, 1, 1, 0]}, "5AING": {"profe": 11, "horas": [5, 1, 5, 0], "dias": [2, 3, 3, 4]}, "5AEFI": {"profe": 15, "horas": [2, 0, 2], "dias": [1, 2, 0]}, "5ANAT": {"profe": 7, "horas": [3, 1, 5], "dias": [1, 2, 1]}, "5ASOC": {"profe": 8, "horas": [3, 1, 0], "dias": [0, 2, 4]}, "5ALIB": {"profe": 17, "horas": [4, 3, 3], "dias": [1, 3, 2]}, "5AREL": {"profe": 4, "horas": [3, 5], "dias": [4, 1]}, "5AART": {"profe": 5, "horas": [5, 1], "dias": [4, 3]}, "5BLEN": {"profe": 5, "horas": [5, 4, 3, 0, 0], "dias": [1, 3, 0, 1, 2]}, "5BMAT": {"profe": 11, "horas": [4, 2, 0, 4, 1], "dias": [0, 4, 1, 3, 4]}, "5BING": {"profe": 10, "horas": [5, 0, 5, 4], "dias": [2, 0, 1, 0]}, "5BEFI": {"profe": 14, "horas": [4, 3, 3], "dias": [3, 4, 0]}, "5BNAT": {"profe": 5, "horas": [1, 4, 0], "dias": [4, 4, 3]}, "5BSOC": {"profe": 12, "horas": [3, 2, 5], "dias": [1, 4, 3]}, "5BLIB": {"profe": 16, "horas": [3, 2, 4], "dias": [0, 1, 4]}, "5BREL": {"profe": 1, "horas": [0, 5], "dias": [2, 4]}, "5BART": {"profe": 7, "horas": [4, 1], "dias": [3, 4]}, "6ALEN": {"profe": 4, "horas": [0, 3, 4, 2, 0], "dias": [1, 3, 0, 0, 2]}, "6AMAT": {"profe": 9, "horas": [2, 2, 0, 1, 3], "dias": [3, 0, 1, 4, 3]}, "6AING": {"profe": 11, "horas": [2, 3, 2, 1], "dias": [3, 4, 2, 2]}, "6AEFI": {"profe": 14, "horas": [0, 4, 4], "dias": [2, 2, 0]}, "6ANAT": {"profe": 9, "horas": [5, 0, 3], "dias": [1, 4, 2]}, "6ASOC": {"profe": 4, "horas": [5, 1, 4], "dias": [0, 1, 1]}, "6ALIB": {"profe": 17, "horas": [5, 5, 3], "dias": [3, 2, 1]}, "6AREL": {"profe": 4, "horas": [1, 5], "dias": [0, 3]}, "6AART": {"profe": 7, "horas": [0, 3], "dias": [4, 2]}, "6BLEN": {"profe": 3, "horas": [4, 0, 1, 2, 2], "dias": [2, 2, 4, 3, 2]}, "6BMAT": {"profe": 2, "horas": [5, 3, 4, 4, 4], "dias": [1, 2, 2, 4, 1]}, "6BING": {"profe": 10, "horas": [4, 4, 3, 3], "dias": [3, 2, 3, 4]}, "6BEFI": {"profe": 14, "horas": [2, 4, 0], "dias": [1, 4, 0]}, "6BNAT": {"profe": 5, "horas": [3, 1, 4], "dias": [2, 2, 1]}, "6BSOC": {"profe": 6, "horas": [2, 3, 2], "dias": [4, 3, 0]}, "6BLIB": {"profe": 17, "horas": [5, 1, 0], "dias": [4, 3, 1]}, "6BREL": {"profe": 4, "horas": [2, 1], "dias": [3, 4]}, "6BART": {"profe": 8, "horas": [5, 3], "dias": [3, 2]}}
PP={"1ALEN": {"profe": 9, "horas": [3, 5, 5, 5, 2], "dias": [3, 1, 2, 4, 0]}, "1AMAT": {"profe": 11, "horas": [1, 5, 1, 0, 2], "dias": [0, 4, 1, 1, 3]}, "1AING": {"profe": 11, "horas": [4, 4, 4, 1], "dias": [2, 0, 4, 4]}, "1AEFI": {"profe": 14, "horas": [1, 0, 5], "dias": [4, 1, 3]}, "1ANAT": {"profe": 7, "horas": [1, 5, 4], "dias": [1, 2, 1]}, "1ASOC": {"profe": 9, "horas": [0, 1, 0], "dias": [3, 4, 0]}, "1ALIB": {"profe": 16, "horas": [2, 1, 5], "dias": [1, 2, 3]}, "1AREL": {"profe": 1, "horas": [2, 0], "dias": [3, 4]}, "1AART": {"profe": 1, "horas": [4, 4], "dias": [3, 1]}, "1BLEN": {"profe": 7, "horas": [4, 2, 3, 0, 1], "dias": [4, 2, 3, 0, 0]}, "1BMAT": {"profe": 6, "horas": [2, 0, 4, 5, 2], "dias": [1, 3, 2, 1, 2]}, "1BING": {"profe": 11, "horas": [3, 2, 5, 5], "dias": [0, 4, 3, 1]}, "1BEFI": {"profe": 14, "horas": [3, 2, 1], "dias": [2, 3, 1]}, "1BNAT": {"profe": 6, "horas": [5, 5, 2], "dias": [2, 3, 0]}, "1BSOC": {"profe": 9, "horas": [2, 2, 5], "dias": [3, 4, 0]}, "1BLIB": {"profe": 16, "horas": [2, 0, 2], "dias": [1, 2, 0]}, "1BREL": {"profe": 1, "horas": [3, 2], "dias": [4, 2]}, "1BART": {"profe": 6, "horas": [4, 1], "dias": [1, 2]}, "2ALEN": {"profe": 5, "horas": [1, 5, 5, 4, 3], "dias": [2, 3, 4, 0, 2]}, "2AMAT": {"profe": 5, "horas": [1, 0, 3, 2, 0], "dias": [1, 3, 3, 4, 0]}, "2AING": {"profe": 13, "horas": [3, 5, 4, 0], "dias": [2, 1, 1, 1]}, "2AEFI": {"profe": 15, "horas": [4, 4, 0], "dias": [2, 1, 4]}, "2ANAT": {"profe": 13, "horas": [4, 5, 3], "dias": [3, 2, 0]}, "2ASOC": {"profe": 3, "horas": [2, 1, 1], "dias": [2, 0, 4]}, "2ALIB": {"profe": 17, "horas": [0, 1, 2], "dias": [2, 3, 1]}, "2AREL": {"profe": 3, "horas": [1, 3], "dias": [1, 4]}, "2AART": {"profe": 14, "horas": [5, 3], "dias": [0, 1]}, "2BLEN": {"profe": 7, "horas": [1, 0, 4, 3, 0], "dias": [2, 1, 0, 0, 3]}, "2BMAT": {"profe": 6, "horas": [0, 0, 3, 4, 3], "dias": [4, 2, 3, 0, 1]}, "2BING": {"profe": 13, "horas": [1, 2, 2, 4], "dias": [1, 4, 0, 4]}, "2BEFI": {"profe": 14, "horas": [2, 1, 0], "dias": [0, 3, 3]}, "2BNAT": {"profe": 7, "horas": [1, 2, 4], "dias": [3, 1, 3]}, "2BSOC": {"profe": 5, "horas": [0, 4, 3], "dias": [4, 1, 0]}, "2BLIB": {"profe": 17, "horas": [3, 5, 3], "dias": [4, 3, 0]}, "2BREL": {"profe": 3, "horas": [5, 3], "dias": [1, 0]}, "2BART": {"profe": 15, "horas": [3, 1], "dias": [1, 3]}, "3ALEN": {"profe": 1, "horas": [4, 5, 3, 1, 0], "dias": [4, 3, 1, 0, 2]}, "3AMAT": {"profe": 6, "horas": [1, 1, 3, 3, 1], "dias": [0, 3, 2, 0, 4]}, "3AING": {"profe": 10, "horas": [4, 5, 1, 4], "dias": [2, 1, 2, 1]}, "3AEFI": {"profe": 14, "horas": [2, 4, 4], "dias": [2, 3, 2]}, "3ANAT": {"profe": 6, "horas": [4, 2, 5], "dias": [3, 4, 4]}, "3ASOC": {"profe": 14, "horas": [5, 3, 2], "dias": [2, 3, 4]}, "3ALIB": {"profe": 17, "horas": [5, 2, 4], "dias": [0, 1, 2]}, "3AREL": {"profe": 1, "horas": [1, 4], "dias": [1, 2]}, "3AART": {"profe": 1, "horas": [3, 2], "dias": [0, 4]}, "3BLEN": {"profe": 1, "horas": [5, 1, 0, 5, 2], "dias": [2, 4, 3, 0, 1]}, "3BMAT": {"profe": 12, "horas": [2, 4, 4, 3, 5], "dias": [4, 2, 3, 1, 4]}, "3BING": {"profe": 12, "horas": [3, 0, 3, 0], "dias": [2, 4, 3, 0]}, "3BEFI": {"profe": 14, "horas": [0, 1, 4], "dias": [0, 0, 1]}, "3BNAT": {"profe": 14, "horas": [4, 0, 4], "dias": [4, 4, 0]}, "3BSOC": {"profe": 1, "horas": [2, 1, 0], "dias": [0, 3, 1]}, "3BLIB": {"profe": 17, "horas": [3, 0, 1], "dias": [4, 2, 1]}, "3BREL": {"profe": 3, "horas": [4, 0], "dias": [0, 4]}, "3BART": {"profe": 10, "horas": [5, 5], "dias": [4, 0]}, "4ALEN": {"profe": 10, "horas": [0, 3, 0, 3, 3], "dias": [4, 1, 3, 4, 3]}, "4AMAT": {"profe": 3, "horas": [3, 4, 3, 2, 0], "dias": [2, 4, 1, 0, 1]}, "4AING": {"profe": 13, "horas": [5, 1, 0, 1], "dias": [4, 2, 3, 0]}, "4AEFI": {"profe": 15, "horas": [1, 2, 5], "dias": [1, 4, 2]}, "4ANAT": {"profe": 8, "horas": [1, 4, 2], "dias": [3, 2, 4]}, "4ASOC": {"profe": 3, "horas": [2, 1, 3], "dias": [3, 2, 3]}, "4ALIB": {"profe": 17, "horas": [1, 3, 5], "dias": [4, 1, 0]}, "4AREL": {"profe": 3, "horas": [5, 0], "dias": [4, 3]}, "4AART": {"profe": 8, "horas": [3, 1], "dias": [0, 2]}, "4BLEN": {"profe": 13, "horas": [0, 2, 3, 0, 3], "dias": [0, 2, 3, 2, 4]}, "4BMAT": {"profe": 8, "horas": [4, 5, 2, 4, 3], "dias": [4, 1, 3, 1, 4]}, "4BING": {"profe": 10, "horas": [0, 3, 2, 0], "dias": [2, 0, 0, 0]}, "4BEFI": {"profe": 15, "horas": [1, 3, 5], "dias": [0, 2, 3]}, "4BNAT": {"profe": 13, "horas": [1, 4, 3], "dias": [3, 0, 1]}, "4BSOC": {"profe": 8, "horas": [5, 5, 4], "dias": [4, 2, 3]}, "4BLIB": {"profe": 16, "horas": [2, 2, 2], "dias": [0, 1, 4]}, "4BREL": {"profe": 3, "horas": [0, 4], "dias": [2, 1]}, "4BART": {"profe": 3, "horas": [5, 5], "dias": [3, 0]}, "5ALEN": {"profe": 8, "horas": [1, 0, 0, 3, 4], "dias": [4, 4, 1, 3, 0]}, "5AMAT": {"profe": 8, "horas": [3, 1, 0, 5, 2], "dias": [2, 0, 3, 0, 1]}, "5AING": {"profe": 10, "horas": [3, 1, 5, 4], "dias": [2, 4, 1, 4]}, "5AEFI": {"profe": 15, "horas": [1, 2, 4], "dias": [4, 1, 3]}, "5ANAT": {"profe": 7, "horas": [1, 3, 5], "dias": [4, 4, 0]}, "5ASOC": {"profe": 2, "horas": [3, 4, 3], "dias": [3, 1, 4]}, "5ALIB": {"profe": 17, "horas": [4, 0, 3], "dias": [3, 2, 1]}, "5AREL": {"profe": 2, "horas": [4, 0], "dias": [2, 1]}, "5AART": {"profe": 7, "horas": [4, 2], "dias": [2, 3]}, "5BLEN": {"profe": 11, "horas": [4, 5, 3, 3, 0], "dias": [3, 2, 1, 2, 3]}, "5BMAT": {"profe": 11, "horas": [1, 2, 2, 0, 3], "dias": [2, 2, 0, 4, 3]}, "5BING": {"profe": 10, "horas": [5, 1, 1, 2], "dias": [1, 3, 0, 3]}, "5BEFI": {"profe": 15, "horas": [2, 0, 2], "dias": [2, 1, 3]}, "5BNAT": {"profe": 2, "horas": [3, 1, 1], "dias": [0, 3, 4]}, "5BSOC": {"profe": 2, "horas": [5, 2, 0], "dias": [1, 0, 4]}, "5BLIB": {"profe": 16, "horas": [5, 0, 3], "dias": [3, 0, 4]}, "5BREL": {"profe": 4, "horas": [5, 5], "dias": [0, 4]}, "5BART": {"profe": 7, "horas": [5, 0], "dias": [4, 2]}, "6ALEN": {"profe": 2, "horas": [5, 4, 0, 2, 4], "dias": [2, 0, 0, 4, 4]}, "6AMAT": {"profe": 9, "horas": [3, 1, 2, 4, 2], "dias": [4, 1, 2, 3, 1]}, "6AING": {"profe": 12, "horas": [4, 0, 1, 2], "dias": [4, 1, 3, 2]}, "6AEFI": {"profe": 15, "horas": [4, 0, 1], "dias": [0, 0, 2]}, "6ANAT": {"profe": 2, "horas": [1, 5, 2], "dias": [1, 0, 3]}, "6ASOC": {"profe": 5, "horas": [0, 2, 4], "dias": [1, 2, 2]}, "6ALIB": {"profe": 17, "horas": [3, 0, 5], "dias": [4, 0, 3]}, "6AREL": {"profe": 2, "horas": [3, 0], "dias": [2, 3]}, "6AART": {"profe": 9, "horas": [1, 5], "dias": [3, 3]}, "6BLEN": {"profe": 9, "horas": [3, 0, 4, 4, 3], "dias": [1, 1, 0, 4, 2]}, "6BMAT": {"profe": 5, "horas": [5, 1, 2, 5, 4], "dias": [2, 0, 1, 0, 3]}, "6BING": {"profe": 12, "horas": [2, 5, 4, 0], "dias": [3, 1, 1, 2]}, "6BEFI": {"profe": 15, "horas": [2, 5, 5], "dias": [0, 1, 4]}, "6BNAT": {"profe": 12, "horas": [1, 1, 1], "dias": [2, 1, 0]}, "6BSOC": {"profe": 12, "horas": [4, 5, 3], "dias": [0, 2, 0]}, "6BLIB": {"profe": 16, "horas": [0, 0, 0], "dias": [2, 4, 0]}, "6BREL": {"profe": 2, "horas": [2, 1], "dias": [2, 2]}, "6BART": {"profe": 5, "horas": [4, 2], "dias": [4, 3]}}
asignaturas_impartidas_x_profesor(PP) 




Profe: 1  total horas: 23  asignaturas: ['1AREL', '1AART', '1BREL', '3ALEN', '3AREL', '3AART', '3BLEN', '3BSOC']
Profe: 2  total horas: 23  asignaturas: ['5ASOC', '5AREL', '5BNAT', '5BSOC', '6ALEN', '6ANAT', '6AREL', '6BREL']
Profe: 3  total horas: 23  asignaturas: ['2ASOC', '2AREL', '2BREL', '3BREL', '4AMAT', '4ASOC', '4AREL', '4BREL', '4BART']
Profe: 4  total horas: 5BREL  asignaturas: ['5BREL']
Profe: 5  total horas: 23  asignaturas: ['2ALEN', '2AMAT', '2BSOC', '6ASOC', '6BMAT', '6BART']
Profe: 6  total horas: 23  asignaturas: ['1BMAT', '1BNAT', '1BART', '2BMAT', '3AMAT', '3ANAT']
Profe: 7  total horas: 23  asignaturas: ['1ANAT', '1BLEN', '2BLEN', '2BNAT', '5ANAT', '5AART', '5BART']
Profe: 8  total horas: 23  asignaturas: ['4ANAT', '4AART', '4BMAT', '4BSOC', '5ALEN', '5AMAT']
Profe: 9  total horas: 23  asignaturas: ['1ALEN', '1ASOC', '1BSOC', '6AMAT', '6AART', '6BLEN']
Profe: 10  total horas: 23  asignaturas: ['3AING', '3BART', '4ALEN', '4BING', '5AING', '5BING']
Profe: 11  total ho

[{9: {'m': ['1ALEN', '1ASOC', '1BSOC', '6AMAT', '6AART', '6BLEN'],
   'total_horas': 23,
   'total_materias': 6}},
 {11: {'m': ['1AMAT', '1AING', '1BING', '5BLEN', '5BMAT'],
   'total_horas': 23,
   'total_materias': 5}},
 {14: {'m': ['1AEFI',
    '1BEFI',
    '2AART',
    '2BEFI',
    '3AEFI',
    '3ASOC',
    '3BEFI',
    '3BNAT'],
   'total_horas': 23,
   'total_materias': 8}},
 {7: {'m': ['1ANAT', '1BLEN', '2BLEN', '2BNAT', '5ANAT', '5AART', '5BART'],
   'total_horas': 23,
   'total_materias': 7}},
 {16: {'m': ['1ALIB', '1BLIB', '4BLIB', '5BLIB', '6BLIB'],
   'total_horas': 15,
   'total_materias': 5}},
 {1: {'m': ['1AREL',
    '1AART',
    '1BREL',
    '3ALEN',
    '3AREL',
    '3AART',
    '3BLEN',
    '3BSOC'],
   'total_horas': 23,
   'total_materias': 8}},
 {6: {'m': ['1BMAT', '1BNAT', '1BART', '2BMAT', '3AMAT', '3ANAT'],
   'total_horas': 23,
   'total_materias': 6}},
 {5: {'m': ['2ALEN', '2AMAT', '2BSOC', '6ASOC', '6BMAT', '6BART'],
   'total_horas': 23,
   'total_materias':

In [0]:



evalua_solucion_profesores(PP,PARAMETROS) 

1095

0.0


3287

In [0]:
PROFES_CURSOS= [ [p,set([m[0] for m,v in PP.items() if v['profe'] == p ])]     for p in PARAMETROS['PROFESORES'] if 'LIB' not in PARAMETROS['PROFESORES'][p] ]
sum([ len(x[1])  for x in PROFES_CURSOS   ])



61

In [0]:
sum([  sum([   int(j)-int(i)   for indi, i in enumerate(sorted(list(x[1]),reverse=True)) for indj,j in enumerate(sorted(list(x[1]),reverse=True)) if indi>indj ])  for indx, x in enumerate(PROFES_CURSOS )])


226

[3, 4, 4, 4, 5, 5, 3, 4, 4, 5, 4, 5, 3, 4, 4]

In [0]:
S4={'1ALEN': {'profe': 5, 'horas': [3, 5, 3, 2, 4], 'dias': [2, 1, 0, 4, 2]}, '1AMAT': {'profe': 6, 'horas': [2, 4, 0, 5, 0], 'dias': [1, 4, 1, 0, 4]}, '1AING': {'profe': 12, 'horas': [4, 1, 5, 0], 'dias': [0, 1, 4, 3]}, '1AEFI': {'profe': 15, 'horas': [4, 5, 0], 'dias': [1, 3, 3]}, '1ANAT': {'profe': 8, 'horas': [2, 5, 0], 'dias': [0, 4, 4]}, '1ASOC': {'profe': 11, 'horas': [4, 3, 4], 'dias': [4, 2, 3]}, '1ALIB': {'profe': 17, 'horas': [5, 0, 3], 'dias': [2, 0, 4]}, '1AREL': {'profe': 3, 'horas': [0, 4], 'dias': [1, 2]}, '1AART': {'profe': 9, 'horas': [5, 1], 'dias': [0, 0]}, '1BLEN': {'profe': 2, 'horas': [1, 3, 0, 1, 2], 'dias': [4, 1, 0, 3, 2]}, '1BMAT': {'profe': 9, 'horas': [2, 5, 2, 4, 1], 'dias': [4, 1, 3, 0, 1]}, '1BING': {'profe': 10, 'horas': [0, 0, 3, 5], 'dias': [2, 0, 3, 4]}, '1BEFI': {'profe': 15, 'horas': [2, 3, 2], 'dias': [4, 2, 1]}, '1BNAT': {'profe': 8, 'horas': [4, 3, 1], 'dias': [4, 4, 4]}, '1BSOC': {'profe': 8, 'horas': [5, 1, 1], 'dias': [3, 0, 2]}, '1BLIB': {'profe': 16, 'horas': [3, 3, 5], 'dias': [3, 0, 2]}, '1BREL': {'profe': 3, 'horas': [3, 0], 'dias': [1, 3]}, '1BART': {'profe': 6, 'horas': [4, 2], 'dias': [2, 0]}, '2ALEN': {'profe': 9, 'horas': [1, 1, 2, 0, 3], 'dias': [2, 3, 2, 1, 4]}, '2AMAT': {'profe': 11, 'horas': [5, 3, 3, 5, 1], 'dias': [2, 3, 4, 1, 3]}, '2AING': {'profe': 10, 'horas': [2, 2, 0, 2], 'dias': [0, 4, 4, 1]}, '2AEFI': {'profe': 14, 'horas': [1, 2, 3], 'dias': [2, 4, 1]}, '2ANAT': {'profe': 6, 'horas': [2, 5, 5], 'dias': [2, 4, 3]}, '2ASOC': {'profe': 11, 'horas': [1, 4, 1], 'dias': [0, 1, 4]}, '2ALIB': {'profe': 17, 'horas': [3, 4, 5], 'dias': [2, 4, 0]}, '2AREL': {'profe': 2, 'horas': [2, 2], 'dias': [3, 0]}, '2AART': {'profe': 15, 'horas': [0, 2], 'dias': [2, 3]}, '2BLEN': {'profe': 7, 'horas': [1, 1, 1, 4, 2], 'dias': [0, 3, 2, 4, 1]}, '2BMAT': {'profe': 1, 'horas': [0, 3, 1, 0, 4], 'dias': [3, 0, 2, 0, 1]}, '2BING': {'profe': 11, 'horas': [3, 0, 5, 4], 'dias': [1, 0, 4, 2]}, '2BEFI': {'profe': 14, 'horas': [0, 4, 2], 'dias': [2, 1, 0]}, '2BNAT': {'profe': 15, 'horas': [2, 4, 3], 'dias': [0, 3, 3]}, '2BSOC': {'profe': 4, 'horas': [0, 4, 1], 'dias': [4, 0, 1]}, '2BLIB': {'profe': 17, 'horas': [5, 3, 2], 'dias': [3, 2, 0]}, '2BREL': {'profe': 3, 'horas': [3, 2], 'dias': [0, 1]}, '2BART': {'profe': 4, 'horas': [4, 3], 'dias': [4, 0]}, '3ALEN': {'profe': 6, 'horas': [3, 1, 1, 3, 3], 'dias': [0, 2, 1, 4, 3]}, '3AMAT': {'profe': 2, 'horas': [4, 2, 1, 1, 0], 'dias': [4, 1, 0, 2, 2]}, '3AING': {'profe': 12, 'horas': [1, 0, 2, 3], 'dias': [4, 2, 1, 1]}, '3AEFI': {'profe': 15, 'horas': [1, 2, 3], 'dias': [2, 2, 0]}, '3ANAT': {'profe': 7, 'horas': [2, 5, 1], 'dias': [3, 2, 1]}, '3ASOC': {'profe': 8, 'horas': [2, 4, 0], 'dias': [2, 0, 1]}, '3ALIB': {'profe': 16, 'horas': [0, 5, 4], 'dias': [4, 0, 3]}, '3AREL': {'profe': 2, 'horas': [4, 3], 'dias': [2, 4]}, '3AART': {'profe': 14, 'horas': [5, 1], 'dias': [4, 0]}, '3BLEN': {'profe': 5, 'horas': [2, 0, 4, 2, 4], 'dias': [1, 3, 4, 2, 0]}, '3BMAT': {'profe': 4, 'horas': [5, 1, 5, 2, 5], 'dias': [3, 2, 0, 2, 2]}, '3BING': {'profe': 11, 'horas': [3, 1, 0, 2], 'dias': [0, 2, 4, 2]}, '3BEFI': {'profe': 14, 'horas': [0, 3, 4], 'dias': [3, 3, 2]}, '3BNAT': {'profe': 6, 'horas': [2, 4, 2], 'dias': [3, 3, 4]}, '3BSOC': {'profe': 15, 'horas': [4, 1, 5], 'dias': [2, 1, 2]}, '3BLIB': {'profe': 16, 'horas': [4, 4, 0], 'dias': [1, 3, 2]}, '3BREL': {'profe': 2, 'horas': [0, 3], 'dias': [4, 0]}, '3BART': {'profe': 2, 'horas': [1, 5], 'dias': [1, 3]}, '4ALEN': {'profe': 7, 'horas': [0, 0, 2, 2, 4], 'dias': [3, 2, 4, 2, 2]}, '4AMAT': {'profe': 7, 'horas': [4, 3, 4, 0, 4], 'dias': [3, 1, 0, 4, 1]}, '4AING': {'profe': 12, 'horas': [0, 0, 5, 5], 'dias': [1, 0, 2, 3]}, '4AEFI': {'profe': 14, 'horas': [2, 2, 3], 'dias': [3, 1, 0]}, '4ANAT': {'profe': 3, 'horas': [1, 1, 3], 'dias': [4, 3, 2]}, '4ASOC': {'profe': 13, 'horas': [3, 3, 3], 'dias': [3, 2, 1]}, '4ALIB': {'profe': 16, 'horas': [5, 5, 5], 'dias': [4, 1, 3]}, '4AREL': {'profe': 2, 'horas': [4, 0], 'dias': [1, 3]}, '4AART': {'profe': 9, 'horas': [3, 4], 'dias': [2, 1]}, '4BLEN': {'profe': 9, 'horas': [4, 4, 3, 0, 1], 'dias': [2, 4, 1, 3, 4]}, '4BMAT': {'profe': 5, 'horas': [1, 1, 5, 3, 5], 'dias': [3, 1, 0, 4, 2]}, '4BING': {'profe': 11, 'horas': [0, 4, 0, 2], 'dias': [3, 0, 2, 4]}, '4BEFI': {'profe': 15, 'horas': [1, 5, 3], 'dias': [0, 0, 1]}, '4BNAT': {'profe': 5, 'horas': [3, 5, 1], 'dias': [1, 4, 2]}, '4BSOC': {'profe': 2, 'horas': [5, 5, 2], 'dias': [0, 1, 4]}, '4BLIB': {'profe': 16, 'horas': [0, 4, 0], 'dias': [0, 3, 1]}, '4BREL': {'profe': 3, 'horas': [4, 2], 'dias': [3, 0]}, '4BART': {'profe': 1, 'horas': [4, 0], 'dias': [2, 4]}, '5ALEN': {'profe': 10, 'horas': [4, 3, 5, 1, 4], 'dias': [0, 4, 3, 0, 4]}, '5AMAT': {'profe': 13, 'horas': [0, 2, 5, 3, 4], 'dias': [1, 3, 1, 4, 1]}, '5AING': {'profe': 13, 'horas': [5, 1, 0, 2], 'dias': [4, 0, 0, 2]}, '5AEFI': {'profe': 14, 'horas': [4, 1, 1], 'dias': [4, 1, 3]}, '5ANAT': {'profe': 8, 'horas': [0, 5, 1], 'dias': [0, 1, 1]}, '5ASOC': {'profe': 10, 'horas': [4, 3, 5], 'dias': [3, 1, 2]}, '5ALIB': {'profe': 16, 'horas': [4, 1, 1], 'dias': [0, 4, 3]}, '5AREL': {'profe': 1, 'horas': [2, 2], 'dias': [1, 4]}, '5AART': {'profe': 9, 'horas': [5, 0], 'dias': [4, 4]}, '5BLEN': {'profe': 6, 'horas': [0, 1, 3, 1, 5], 'dias': [0, 4, 2, 3, 1]}, '5BMAT': {'profe': 3, 'horas': [5, 3, 4, 2, 4], 'dias': [4, 3, 0, 3, 4]}, '5BING': {'profe': 13, 'horas': [5, 5, 2, 1], 'dias': [2, 3, 1, 3]}, '5BEFI': {'profe': 14, 'horas': [5, 0, 3], 'dias': [1, 1, 4]}, '5BNAT': {'profe': 7, 'horas': [3, 5, 2], 'dias': [3, 0, 0]}, '5BSOC': {'profe': 13, 'horas': [0, 3, 1], 'dias': [3, 0, 1]}, '5BLIB': {'profe': 17, 'horas': [1, 4, 0], 'dias': [0, 1, 2]}, '5BREL': {'profe': 1, 'horas': [4, 3], 'dias': [3, 1]}, '5BART': {'profe': 1, 'horas': [3, 3], 'dias': [4, 2]}, '6ALEN': {'profe': 8, 'horas': [2, 2, 1, 5, 3], 'dias': [4, 3, 3, 0, 2]}, '6AMAT': {'profe': 5, 'horas': [5, 2, 2, 1, 0], 'dias': [3, 0, 3, 0, 1]}, '6AING': {'profe': 10, 'horas': [1, 2, 4, 1], 'dias': [4, 3, 2, 1]}, '6AEFI': {'profe': 14, 'horas': [2, 5, 0], 'dias': [2, 2, 0]}, '6ANAT': {'profe': 4, 'horas': [5, 3, 0], 'dias': [4, 3, 0]}, '6ASOC': {'profe': 10, 'horas': [5, 0, 2], 'dias': [1, 3, 2]}, '6ALIB': {'profe': 16, 'horas': [4, 4, 0], 'dias': [0, 3, 2]}, '6AREL': {'profe': 1, 'horas': [0, 2], 'dias': [1, 3]}, '6AART': {'profe': 7, 'horas': [5, 0], 'dias': [1, 1]}, '6BLEN': {'profe': 1, 'horas': [1, 0, 2, 5, 5], 'dias': [3, 2, 0, 2, 0]}, '6BMAT': {'profe': 3, 'horas': [5, 3, 1, 4, 5], 'dias': [0, 4, 0, 1, 1]}, '6BING': {'profe': 13, 'horas': [1, 1, 2, 4], 'dias': [4, 2, 0, 2]}, '6BEFI': {'profe': 15, 'horas': [0, 0, 1], 'dias': [1, 4, 4]}, '6BNAT': {'profe': 8, 'horas': [3, 4, 4], 'dias': [3, 3, 1]}, '6BSOC': {'profe': 1, 'horas': [3, 4, 1], 'dias': [3, 0, 4]}, '6BLIB': {'profe': 16, 'horas': [2, 3, 2], 'dias': [1, 2, 4]}, '6BREL': {'profe': 3, 'horas': [0, 5], 'dias': [4, 3]}, '6BART': {'profe': 9, 'horas': [3, 0], 'dias': [0, 2]}}

analiza_solucion(S4,PARAMETROS)['REPETIDAS']
asignaturas_impartidas_x_profesor(S4) 
 
	 

Profe: 1  total horas: 23  asignaturas: ['2BMAT', '4BART', '5AREL', '5BREL', '5BART', '6AREL', '6BLEN', '6BSOC']
Profe: 2  total horas: 23  asignaturas: ['1BLEN', '2AREL', '3AMAT', '3AREL', '3BREL', '3BART', '4AREL', '4BSOC']
Profe: 3  total horas: 23  asignaturas: ['1AREL', '1BREL', '2BREL', '4ANAT', '4BREL', '5BMAT', '6BMAT', '6BREL']
Profe: 4  total horas: 13  asignaturas: ['2BSOC', '2BART', '3BMAT', '6ANAT']
Profe: 5  total horas: 23  asignaturas: ['1ALEN', '3BLEN', '4BMAT', '4BNAT', '6AMAT']
Profe: 6  total horas: 23  asignaturas: ['1AMAT', '1BART', '2ANAT', '3ALEN', '3BNAT', '5BLEN']
Profe: 7  total horas: 23  asignaturas: ['2BLEN', '3ANAT', '4ALEN', '4AMAT', '5BNAT', '6AART']
Profe: 8  total horas: 23  asignaturas: ['1ANAT', '1BNAT', '1BSOC', '3ASOC', '5ANAT', '6ALEN', '6BNAT']
Profe: 9  total horas: 23  asignaturas: ['1AART', '1BMAT', '2ALEN', '4AART', '4BLEN', '5AART', '6BART']
Profe: 10  total horas: 23  asignaturas: ['1BING', '2AING', '5ALEN', '5ASOC', '6AING', '6ASOC']
Prof

[{5: {'m': ['1ALEN', '3BLEN', '4BMAT', '4BNAT', '6AMAT'],
   'total_horas': 23,
   'total_materias': 5}},
 {6: {'m': ['1AMAT', '1BART', '2ANAT', '3ALEN', '3BNAT', '5BLEN'],
   'total_horas': 23,
   'total_materias': 6}},
 {12: {'m': ['1AING', '3AING', '4AING'],
   'total_horas': 12,
   'total_materias': 3}},
 {15: {'m': ['1AEFI',
    '1BEFI',
    '2AART',
    '2BNAT',
    '3AEFI',
    '3BSOC',
    '4BEFI',
    '6BEFI'],
   'total_horas': 23,
   'total_materias': 8}},
 {8: {'m': ['1ANAT', '1BNAT', '1BSOC', '3ASOC', '5ANAT', '6ALEN', '6BNAT'],
   'total_horas': 23,
   'total_materias': 7}},
 {11: {'m': ['1ASOC', '2AMAT', '2ASOC', '2BING', '3BING', '4BING'],
   'total_horas': 23,
   'total_materias': 6}},
 {17: {'m': ['1ALIB', '2ALIB', '2BLIB', '5BLIB'],
   'total_horas': 12,
   'total_materias': 4}},
 {3: {'m': ['1AREL',
    '1BREL',
    '2BREL',
    '4ANAT',
    '4BREL',
    '5BMAT',
    '6BMAT',
    '6BREL'],
   'total_horas': 23,
   'total_materias': 8}},
 {9: {'m': ['1AART', '1BMAT',

In [0]:
 def imprime_horarios_profesores(SOLUCION_INPUT, PARAMETROS):

  HORARIOS_PROFES = {k:np.array([[np.array("")]*6]*5,dtype=object) for k in PARAMETROS['PROFESORES'] }

  #print(HORARIOS_PROFES)

  #HORARIOS[k[0:2]][v['dias'][i]][v['horas'][i]]

  for m,v  in SOLUCION_INPUT.items():
    #print(m,v)
    for i in range(len(v['dias'])):
      HORARIOS_PROFES[v['profe']][v['dias'][i]][v['horas'][i]] = m

  print(analiza_solucion(SOLUCION_INPUT,PARAMETROS)['LIBRES'])
     
  for p in [k for k,v in PARAMETROS['PROFESORES'].items() if 'LIB' not in v ] :
  
    print("\n\n", p, "\n----------------------------------------------------------------------------------------------------")
    print(   "  L       \tM       \tX       \tJ       \tV       ")
    print(    "----------------------------------------------------------------------------------------------------")

    for h in range(PARAMETROS['HORAS']):
      #print(HORARIOS_PROFES[p])
      print('\t')
      for d  in range(5):
        print(   HORARIOS_PROFES[p][d][h]   if HORARIOS_PROFES[p][d][h]  else "---"  , '\t\t' ,end=""  )
      


  
      print()
     
  

  return

imprime_horarios_profesores(PP,PARAMETROS)  

{1: ['0-0', '0-4', '1-5', '2-1', '2-3', '3-3', '4-5'], 2: ['0-1', '1-2', '1-3', '2-0', '3-4', '3-5', '4-5'], 3: ['0-0', '1-2', '2-4', '2-5', '3-1', '3-4', '4-2'], 4: ['0-0', '0-1', '0-2', '0-3', '0-4', '1-0', '1-1', '1-2', '1-3', '1-4', '1-5', '2-0', '2-1', '2-2', '2-3', '2-4', '2-5', '3-0', '3-1', '3-2', '3-3', '3-4', '3-5', '4-0', '4-1', '4-2', '4-3', '4-4'], 5: ['0-2', '1-3', '1-5', '2-0', '3-1', '4-1', '4-3'], 6: ['0-0', '0-5', '1-0', '1-1', '3-2', '4-3', '4-4'], 7: ['0-2', '1-3', '1-5', '2-3', '3-5', '4-0', '4-2'], 8: ['0-0', '0-2', '1-1', '1-3', '2-0', '2-2', '3-5'], 9: ['0-1', '0-3', '1-4', '2-0', '2-1', '2-4', '4-0'], 10: ['0-4', '1-0', '1-1', '1-2', '2-2', '2-5', '3-4', '3-5', '4-2'], 11: ['0-0', '0-5', '1-2', '1-4', '2-0', '3-1', '4-3'], 12: ['0-2', '0-5', '1-2', '3-0', '3-5', '4-1', '4-3'], 13: ['0-5', '1-2', '2-4', '3-2', '3-5', '4-0', '4-1'], 14: ['0-3', '1-2', '1-5', '2-0', '2-1', '4-3', '4-5'], 15: ['0-3', '0-5', '2-0', '3-0', '3-3', '4-3', '4-4'], 16: ['0-0', '0-1', '0-

In [0]:
#Busqueda por mejor solucion local
#Se buscan mejores soluciones intercambiando materias dentro de cada dia/curso  
#NO ES NECESARIA
def mejor_solucion_local(SOLUCION, PARAMETROS):
  
  MEJOR_SOLUCION = copy.deepcopy(SOLUCION)
  MEJOR_VALOR = evalua_solucion_horarios( MEJOR_SOLUCION, PARAMETROS  )
  #print("Valor inicial", MEJOR_VALOR, SOLUCION)

  HORARIOS = convierte_a_horarios(SOLUCION,PARAMETROS)
  
  #print(SOLUCION) 
  #print(HORARIOS)
   
 
  #Recorre todas los cursos(curso/letra)
  for k,v in HORARIOS.items():
      #print(k)
      for inxd,d in enumerate(v):

        #Para cada dia se intercambian los posibles horarios
        #print("-->", "dia:", d)
        for i in range(len(d)):
          for j in range(i+1,len(d)-1):
            #print("\t Intercambia ", i , " con " , j, )
            SOLUCION_COPIA = copy.deepcopy(SOLUCION)
            materia1=""
            materia2=""
            if HORARIOS[k][inxd][i]:
              materia1 = HORARIOS[k][inxd][i][0]
              posicion_dia_i = [indice  for indice, _dia in  enumerate(SOLUCION_COPIA[k+materia1]['dias']) if _dia == inxd  ][0]
            
            #print("--->", np.array(HORARIOS[k][inxd][j]), )
            #print(np.array(HORARIOS[k][inxd][j]).shape[0] or "" )

            if  np.array(HORARIOS[k][inxd][j])  :
              materia2 = HORARIOS[k][inxd][j][0]
              posicion_dia_j = [indice  for indice, _dia in  enumerate(SOLUCION_COPIA[k+materia2]['dias']) if _dia == inxd  ][0]

            
            
            #Se hace el intercambio solo si existen las dos materias. MEJORA hacer el intercambio tambien con horas vacias
            if materia1 and materia2:
              #print("\t Materias ", materia1 , " con " , materia2, )
              #print("\t Posiciones",posicion_dia_i, posicion_dia_j ,"\n" )
              SOLUCION_COPIA[k+materia1]['horas'] = SOLUCION_COPIA[k+materia1]['horas'][0:posicion_dia_i]+[j]+SOLUCION_COPIA[k+materia1]['horas'][posicion_dia_i+1:]
              SOLUCION_COPIA[k+materia2]['horas'] = SOLUCION_COPIA[k+materia2]['horas'][0:posicion_dia_j]+[i]+SOLUCION_COPIA[k+materia2]['horas'][posicion_dia_j+1:]
              #print("\t", SOLUCION )
              #print("\t", SOLUCION_COPIA) 

            #La segunda hora esta libre
            if materia1 and not materia2:
              SOLUCION_COPIA[k+materia1]['horas'] = SOLUCION_COPIA[k+materia1]['horas'][0:posicion_dia_i]+[j]+SOLUCION_COPIA[k+materia1]['horas'][posicion_dia_i+1:]
            #La primera hora esta libre
            if not materia1 and  materia2:
              SOLUCION_COPIA[k+materia2]['horas'] = SOLUCION_COPIA[k+materia2]['horas'][0:posicion_dia_j]+[i]+SOLUCION_COPIA[k+materia2]['horas'][posicion_dia_j+1:]


            VALOR_COPIA = evalua_solucion_horarios( SOLUCION_COPIA, PARAMETROS  )
            
            if VALOR_COPIA < MEJOR_VALOR:
              #print("Encontrada mejor solucion con valor:" , VALOR_COPIA, SOLUCION_COPIA)
              MEJOR_SOLUCION = copy.deepcopy(SOLUCION_COPIA)
              MEJOR_VALOR = VALOR_COPIA

      #signaturas_impartidas_x_profesor(SOLUCION_COPIA)
      #print()

    #print("Valor final", MEJOR_VALOR, evalua_solucion_horarios( MEJOR_SOLUCION, PARAMETROS  ))
    #print("Valor inicial", MEJOR_VALOR, MEJOR_SOLUCION)
 

  return MEJOR_SOLUCION



In [0]:




mejor_solucion_local_profesores(PP, PARAMETROS)